# All results used in the paper have been computed here

Run on a vast.ai instance with an RTX 4090 and 21CPU/128 of a AMD EPYC 7B13 + 43Gb RAM

Use cuda latest image to run

Fixed version of python cuda drivers as recent release of cuda 12.6 is available on python package but not yet in docker image 

All class are written here directly and do not use the package as it has been done before. (TLN is refered as Linear Net in this notebook)

In [1]:
!apt update -y

Hit:1 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  InRelease
Get:2 http://security.ubuntu.com/ubuntu jammy-security InRelease [129 kB]
Hit:3 http://archive.ubuntu.com/ubuntu jammy InRelease 
Get:4 http://archive.ubuntu.com/ubuntu jammy-updates InRelease [128 kB]
Hit:5 http://archive.ubuntu.com/ubuntu jammy-backports InRelease    33m
Fetched 257 kB in 1s (246 kB/s)
Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
All packages are up to date.


In [2]:
!apt upgrade -y

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
Calculating upgrade... Done
0 upgraded, 0 newly installed, 0 to remove and 0 not upgraded.


In [3]:
!apt upgrade libnccl2 -y --allow-change-held-packages

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
libnccl2 is already the newest version (2.22.3-1+cuda12.6).
Calculating upgrade... Done
0 upgraded, 0 newly installed, 0 to remove and 0 not upgraded.


In [4]:
!git clone https://github.com/zhouhaoyi/ETDataset.git

fatal: destination path 'ETDataset' already exists and is not an empty directory.


In [5]:
!pip install -U pandas==2.2.2 numpy==1.26.4 matplotlib pyarrow==17.0.0 scikit-learn==1.5.1 tkan==0.4.1 "jax[cuda12]"==0.4.30 nvidia-cublas-cu12==12.5.3.2 nvidia-cuda-cupti-cu12==12.5.82 nvidia-cuda-nvcc-cu12==12.5.82 nvidia-cuda-runtime-cu12==12.5.82 nvidia-nvjitlink-cu12==12.5.82 nvidia-cusolver-cu12==11.6.3.83 nvidia-cusparse-cu12==12.5.1.3 nvidia-cufft-cu12==11.2.3.61

In [6]:
import os
BACKEND = 'jax' # You can use any backend here 
os.environ['KERAS_BACKEND'] = BACKEND

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

from typing import Optional, Union, List

import keras
from keras import layers
from keras.models import Sequential, Model
from keras.layers import LSTM, Dense, Input, Flatten, GRU, Layer, Conv1D, RepeatVector, TimeDistributed, Permute, AveragePooling1D, Dropout, LayerNormalization, BatchNormalization


from sklearn.metrics import r2_score, root_mean_squared_error
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LinearRegression, Ridge

from tkan import TKAN

import time

keras.utils.set_random_seed(1) 

N_MAX_EPOCHS = 1000
BATCH_SIZE = 128
early_stopping_callback = lambda : keras.callbacks.EarlyStopping(
    monitor="val_loss",
    min_delta=0.00001,
    patience=10,
    mode="min",
    restore_best_weights=True,
    start_from_epoch=6,
)
lr_callback = lambda : keras.callbacks.ReduceLROnPlateau(
    monitor="val_loss",
    factor=0.25,
    patience=5,
    mode="min",
    min_delta=0.00001,
    min_lr=0.000025,
    verbose=0,
)
callbacks = lambda : [early_stopping_callback(), lr_callback(), keras.callbacks.TerminateOnNaN()]


## CLinear, NLinear and DLinear from "Are Transformers Effective for Time Series Forecasting?" in Keras3

In [7]:

class CLinear(Layer):
    """
    C for classic
    Just one Linear layer
    """
    def __init__(self, pred_len, individual=False, **kwargs):
        super().__init__(**kwargs)
        self.pred_len = pred_len
        self.Linear = Dense(self.pred_len)

    def build(self, input_shape):
        
        super().build(input_shape)

    def call(self, x):

        x = keras.ops.transpose(x, [0, 2, 1])
        x = self.Linear(x)
        x = keras.ops.transpose(x, [0, 2, 1])
        
        return x # [Batch, Output length, Channel]

class NLinear(Layer):
    """
    N for Normalized
    Just one Linear layer
    """
    def __init__(self, pred_len, individual=False, **kwargs):
        super().__init__(**kwargs)
        self.pred_len = pred_len
        self.individual = individual
        self.Linear = None

    def build(self, input_shape):
        seq_len, channels = input_shape[1], input_shape[2]
        if self.individual:
            self.Linear = [Dense(self.pred_len) for _ in range(channels)]
        else:
            self.Linear = Dense(self.pred_len)
        super().build(input_shape)

    def call(self, x):
        # x: [Batch, Input length, Channel]
        last_seq = x[:,-1:,:]
        x = x - last_seq
        if self.individual:
            outputs = [layer(x[:,:,i]) for i, layer in enumerate(self.Linear)]
            x = keras.ops.stack(outputs, axis=-1)
        else:
            x = keras.ops.transpose(x, [0, 2, 1])
            x = self.Linear(x)
            x = keras.ops.transpose(x, [0, 2, 1])
        
        return x + last_seq# [Batch, Output length, Channel]


class MovingAvg(Layer):
    def __init__(self, kernel_size, stride=1, **kwargs):
        super(MovingAvg, self).__init__(**kwargs)
        self.kernel_size = kernel_size
        self.stride = stride

    def build(self, input_shape):
        self.avg = AveragePooling1D(pool_size=self.kernel_size, strides=self.stride, padding='valid')

    def call(self, x):
        front = keras.ops.repeat(x[:, 0:1, :], (self.kernel_size - 1) // 2, axis=1)
        end = keras.ops.repeat(x[:, -1:, :], (self.kernel_size - 1) // 2, axis=1)
        x = keras.ops.concatenate([front, x, end], axis=1)
        return self.avg(x)

class SeriesDecomp(Layer):
    def __init__(self, kernel_size, **kwargs):
        super(SeriesDecomp, self).__init__(**kwargs)
        self.moving_avg = MovingAvg(kernel_size, stride=1)

    def call(self, x):
        moving_mean = self.moving_avg(x)
        res = x - moving_mean
        return res, moving_mean

class DLinear(Layer):
    def __init__(self, pred_len, individual=False, **kwargs):
        super().__init__(**kwargs)
        self.pred_len = pred_len
        self.individual = individual
        self.kernel_size = 5
        self.decomposition = SeriesDecomp(self.kernel_size)

    def build(self, input_shape):
        self.seq_len = input_shape[1]
        self.channels = input_shape[2]
        
        if self.individual:
            self.linear_seasonal = [Dense(self.pred_len) for _ in range(self.channels)]
            self.linear_trend = [Dense(self.pred_len) for _ in range(self.channels)]
        else:
            self.linear_seasonal = Dense(self.pred_len)
            self.linear_trend = Dense(self.pred_len)

        super().build(input_shape)

    def call(self, x):
        seasonal_init, trend_init = self.decomposition(x)
        seasonal_init = keras.ops.transpose(seasonal_init, (0, 2, 1))
        trend_init = keras.ops.transpose(trend_init, (0, 2, 1))
        if self.individual:
            seasonal_output = keras.ops.stack([self.linear_seasonal[i](seasonal_init[:, i, :]) 
                                               for i in range(self.channels)], axis=1)
            trend_output = keras.ops.stack([self.linear_trend[i](trend_init[:, i, :]) 
                                            for i in range(self.channels)], axis=1)
        else:
            seasonal_output = self.linear_seasonal(seasonal_init)
            trend_output = self.linear_trend(trend_init)
        
        return keras.ops.transpose(seasonal_output + trend_output, (0, 2, 1))

# TSMixer: An All-MLP Architecture for Time Series Forecasting

In [8]:

class TSMixer_RevNorm(Layer):
    """Reversible Instance Normalization."""
    
    def __init__(self, axis, eps=1e-5, affine=True):
        super().__init__()
        self.axis = axis
        self.eps = eps
        self.affine = affine
        
    def build(self, input_shape):
        if self.affine:
            self.affine_weight = self.add_weight(
              name='affine_weight', shape=(input_shape[-1],), initializer='ones'
            )
            self.affine_bias = self.add_weight(
              name='affine_bias', shape=(input_shape[-1],), initializer='zeros'
            )
    
    def call(self, x, mode = 'norm', mean = None, stdev = None, target_slice=None):
        if mode == 'norm':
            mean = keras.ops.stop_gradient(
                keras.ops.mean(x, axis=self.axis, keepdims=True)
            )
            stdev = keras.ops.stop_gradient(
                keras.ops.sqrt(
                    keras.ops.var(x, axis=self.axis, keepdims=True) + self.eps
                    )
            )
            normalized = self._normalize(x, mean, stdev)
            return normalized, mean, stdev
        elif mode == 'denorm':
            return self._denormalize(x, mean, stdev, target_slice)
        else:
            raise NotImplementedError
        

    def _normalize(self, x, mean, stdev):
        x = x - mean
        x = x / stdev
        if self.affine:
            x = x * self.affine_weight
            x = x + self.affine_bias
        return x

    def _denormalize(self, x, mean, stdev, target_slice=None):
        if self.affine:
            x = x - self.affine_bias[target_slice]
            x = x / self.affine_weight[target_slice]
        if target_slice is not None:
            x = x * stdev[..., target_slice]
            x = x + mean[..., target_slice]
        else:
            x = x * stdev
            x = x + mean
        return x

def TSMixer_res_block(inputs, norm_type, activation, dropout, ff_dim):
    """Residual block of TSMixer."""
    
    norm = (
      LayerNormalization(axis=[-2, -1])
      if norm_type == 'L'
      else BatchNormalization()
    )
    
    # Temporal Linear
    x = norm(inputs)
    x = Permute([2, 1])(x)  # [Batch, Channel, Input Length]
    x = Dense(x.shape[-1], activation=activation)(x)
    x = Permute([2, 1])(x)  # [Batch, Input Length, Channel]
    x = Dropout(dropout)(x)
    res = x + inputs
    
    # Feature Linear
    x = norm(res)
    x = Dense(ff_dim, activation=activation)(x)  # [Batch, Input Length, FF_Dim]
    x = Dropout(dropout)(x)
    x = Dense(inputs.shape[-1])(x)  # [Batch, Input Length, Channel]
    x = Dropout(dropout)(x)
    return x + res


def TSMixer(
        input_shape,
        pred_len,
        norm_type,
        activation,
        n_block,
        dropout,
        ff_dim,
        target_slice = None,
    ):
    """Build TSMixer with Reversible Instance Normalization model."""
    inputs = keras.Input(shape=input_shape)
    x = inputs  # [Batch, Input Length, Channel]
    rev_norm = TSMixer_RevNorm(axis=-2)
    x, mean, stdev = rev_norm(x, mode = 'norm')
    for _ in range(n_block):
        x = TSMixer_res_block(x, norm_type, activation, dropout, ff_dim)
    if target_slice:
        x = x[:, :, target_slice]
    
    x = Permute([2, 1])(x)  # [Batch, Channel, Input Length]
    x = Dense(pred_len)(x)  # [Batch, Channel, Output Length]
    outputs = Permute([2, 1])(x)  # [Batch, Output Length, Channel])
    outputs = rev_norm(outputs, mean = mean, stdev = stdev, mode='denorm', target_slice=target_slice)
    return keras.Model(inputs, outputs)


# LinearNet

In [9]:
class SequentialDense(Layer):
    """
    A custom layer that performs sequential dense operations.

    This layer applies dense transformations along both the feature and time dimensions
    of the input sequence.

    Args:
        end_features (int): The number of output features.
        end_sequence_length (int): The length of the output sequence.
        activation (str or callable, optional): Activation function to use. Defaults to 'linear'.
        it_kernel_initializer (keras.initializers.Initializer, optional): Initializer for the input-time kernel. Defaults to RandomUniform(0,1).
        f_kernel_initializer (keras.initializers.Initializer, optional): Initializer for the feature kernel. Defaults to RandomUniform(0,1).
        ot_kernel_initializer (keras.initializers.Initializer, optional): Initializer for the output-time kernel. Defaults to RandomUniform(0,1).
        kernel_regularizer (keras.regularizers.Regularizer, optional): Regularizer function applied to the kernels. Defaults to None.
        **kwargs: Additional keyword arguments passed to the parent Layer class.
    """
    def __init__(self, end_features, end_sequence_length, activation='linear',
                 it_kernel_initializer=keras.initializers.RandomUniform(minval=0.0, maxval=1.0),
                 f_kernel_initializer=keras.initializers.RandomUniform(minval=0.0, maxval=1.0),
                 ot_kernel_initializer=keras.initializers.RandomUniform(minval=0.0, maxval=1.0),
                 kernel_regularizer=None, **kwargs):
        super().__init__(**kwargs)
        self.end_features = end_features
        self.activation = keras.activations.get(activation)
        self.end_sequence_length = end_sequence_length
        self.dense_features = Dense(end_features)
        self.dense_times = Dense(end_sequence_length)
        self.it_kernel_initializer = keras.initializers.get(it_kernel_initializer)
        self.f_kernel_initializer = keras.initializers.get(f_kernel_initializer)
        self.ot_kernel_initializer = keras.initializers.get(ot_kernel_initializer)
        self.kernel_regularizer = keras.regularizers.get(kernel_regularizer)

    def build(self, input_shape):
        _, seq_len, n_features = input_shape
        self.it_kernel = self.add_weight(
            shape=(1, seq_len, 1),
            name="it_kernel",
            initializer=self.it_kernel_initializer,
            regularizer=self.kernel_regularizer,
        )
        self.f_kernel = self.add_weight(
            shape=(1, 1, self.end_features),
            name="f_kernel",
            initializer=self.f_kernel_initializer,
            regularizer=self.kernel_regularizer,
        )
        self.ot_kernel = self.add_weight(
            shape=(1, self.end_sequence_length, 1),
            name="ot_kernel",
            initializer=self.ot_kernel_initializer,
            regularizer=self.kernel_regularizer,
        )
        self.dense_features.build(input_shape)
        self.dense_times.build((input_shape[0], self.end_features, seq_len))
        super().build(input_shape)

    def call(self, inputs):
        x = inputs * self.it_kernel
        x = self.dense_features(x)
        x = x * self.f_kernel
        x = keras.ops.transpose(x, (0, 2, 1))
        x = self.dense_times(x)
        x = keras.ops.transpose(x, (0, 2, 1))
        x = self.ot_kernel * x
        return self.activation(x)

    def compute_output_shape(self, input_shape):
        return (input_shape[0], self.end_sequence_length, self.end_features)

class LinearLayer(Layer):
    """
    A custom layer that applies a linear transformation using pre-computed weights and biases.

    Args:
        equivalent_weights (np.ndarray): Pre-computed weights for the linear transformation.
        equivalent_bias (np.ndarray): Pre-computed bias for the linear transformation.
        **kwargs: Additional keyword arguments passed to the parent Layer class.
    """
    def __init__(self, equivalent_weights, equivalent_bias, **kwargs):
        super().__init__(**kwargs)
        self.equivalent_weights = self.add_weight(
            shape=equivalent_weights.shape,
            initializer=keras.initializers.Constant(equivalent_weights),
            trainable=False,
            name='equivalent_weights'
        )
        self.equivalent_bias = self.add_weight(
            shape=equivalent_bias.shape,
            initializer=keras.initializers.Constant(equivalent_bias),
            trainable=False,
            name='equivalent_bias'
        )

    def call(self, inputs):
        return keras.ops.einsum('bij,ijkl->bkl', inputs, self.equivalent_weights) + self.equivalent_bias

    def get_config(self):
        config = super().get_config()
        config.update({
            "equivalent_weights": keras.ops.convert_to_numpy(self.equivalent_weights),
            "equivalent_bias": keras.ops.convert_to_numpy(self.equivalent_bias)
        })
        return config

class LinearNet(keras.Model):
    """
    A custom model that applies a series of linear transformations to the input.

    Args:
        output_len (int): The length of the output sequence.
        output_features (int, optional): The number of output features. Defaults to 1.
        flatten_output (bool, optional): Whether to flatten the output. Defaults to False.
        hidden_layers (int, optional): The number of hidden layers. Defaults to 1.
        use_convolution (bool, optional): Whether to use convolution layers. Defaults to True.
        hidden_sizes (List[int], optional): List of hidden layer sizes. If not provided, sizes will be calculated at build time.
        kernel_size (Union[int, List[int]], optional): Kernel size(s) for convolution layers. Defaults to 5.
        **kwargs: Additional keyword arguments passed to the parent Model class.
    """
    def __init__(self,
                 output_len: int,
                 output_features: int = 1,
                 flatten_output: bool = False,
                 hidden_layers: int = 1,
                 use_convolution: bool = True,
                 hidden_sizes: Optional[List[int]] = None,
                 kernel_size: Optional[Union[int, List[int]]] = 5,
                 **kwargs):
        super().__init__(**kwargs)
        self.output_len = output_len
        self.output_features = output_features
        self.flatten_output = flatten_output
        self.hidden_layers = hidden_layers
        self.use_convolution = use_convolution
        self.hidden_sizes = hidden_sizes
        self.kernel_size = kernel_size

        # Process kernel_size
        if isinstance(kernel_size, (list, tuple)):
            if len(kernel_size) != hidden_layers:
                raise ValueError(f"Received {len(kernel_size)} values in kernel_size while having {hidden_layers} hidden layers. Please provide the same number of values or only provide one integer if you want to use the same everywhere.")
            self.kernel_size = kernel_size
        else:
            self.kernel_size = [kernel_size] * hidden_layers

        # Layers will be defined in the build method
        self.layers_list = []

    def build(self, input_shape):
        _, self.input_seq_len, self.input_features = input_shape

        # Calculate hidden sizes if not provided
        if self.hidden_sizes is None:
            self.hidden_sizes = [
                int(self.input_features - (i + 1) * (self.output_features - self.input_features) / self.hidden_layers)
                for i in range(self.hidden_layers)
            ]
        elif len(self.hidden_sizes) != self.hidden_layers:
            raise ValueError(f"Received {len(self.hidden_sizes)} values in hidden_sizes while having {self.hidden_layers} hidden layers. Please provide the same number of values.")

        # Define layers
        for i in range(self.hidden_layers):
            if i == self.hidden_layers - 1:
                hidden_size = self.output_features
            else:
                hidden_size = self.hidden_sizes[i]
            
            if self.use_convolution:
                self.layers_list.append(SequentialDense(
                    end_features=hidden_size,
                    end_sequence_length=int(self.output_len + self.kernel_size[i] - 1)
                ))
                self.layers_list.append(Conv1D(
                    filters=self.output_features,
                    kernel_size=self.kernel_size[i],
                    padding='valid'
                ))
            else:
                self.layers_list.append(SequentialDense(
                    end_features=hidden_size,
                    end_sequence_length=self.output_len
                ))

        if self.flatten_output:
            self.layers_list.append(Flatten())

        # Build all layers
        for layer in self.layers_list:
            layer.build(input_shape)
            input_shape = layer.compute_output_shape(input_shape)

        super().build(input_shape)

    def call(self, inputs):
        x = inputs
        for layer in self.layers_list:
            x = layer(x)
        return x

    def compute_linear_equivalent_weights(self):
        equivalent_weights = keras.ops.zeros((self.input_seq_len, self.input_features, self.output_len, self.output_features))
        equivalent_bias = self.call(keras.ops.zeros((1, self.input_seq_len, self.input_features)))[0]
    
        for i in range(self.input_seq_len):
            for j in range(self.input_features):
                input_tensor = keras.ops.zeros((1, self.input_seq_len, self.input_features))
                input_tensor = input_tensor.at[0, i, j].set(1.0)
                output = self.call(input_tensor)
                equivalent_weights = equivalent_weights.at[i, j].set(output[0] - equivalent_bias)
    
        return equivalent_weights, equivalent_bias

    def get_linear_equivalent_model(self):
        equivalent_weights, equivalent_bias = self.compute_linear_equivalent_weights()
        
        input_layer = Input(shape=(self.input_seq_len, self.input_features))
        linear_layer = LinearLayer(equivalent_weights, equivalent_bias)
        output = linear_layer(input_layer)
        
        linear_model = keras.Model(inputs=input_layer, outputs=output)
        
        # Freeze the model
        linear_model.trainable = False
        
        return linear_model

# Simple LSTM Encoder-Decoder architecture with shared or not shared networks

In [10]:


def create_lstm_encoder_decoder(input_shape, n_ahead, lstm_units=50, flatten_output = False):
    # Input shape should be (sequence_length, n_features)
    encoder_inputs = Input(shape=input_shape)
    
    # Encoder
    encoder = LSTM(lstm_units, activation='tanh', return_state=True)
    encoder_outputs, state_h, state_c = encoder(encoder_inputs)
    
    # We discard `encoder_outputs` and only keep the states.
    encoder_states = [state_h, state_c]
    
    # Set up the decoder, using `encoder_states` as initial state.
    decoder_inputs = RepeatVector(n_ahead)(encoder_outputs)
    
    # We set up our decoder to return full output sequences,
    # and to return internal states as well. We don't use the
    # return states in the training model, but we will use them in inference.
    decoder_lstm = LSTM(lstm_units, activation='tanh', return_sequences=True, return_state=True)
    decoder_outputs, _, _ = decoder_lstm(decoder_inputs, initial_state=encoder_states)
    
    # Dense layer to turn decoder outputs into predictions
    decoder_dense = Dense(1)
    decoder_outputs = decoder_dense(decoder_outputs)

    if flatten_output:
        decoder_outputs = Flatten()(decoder_outputs)
    # Define the model that will turn
    # `encoder_input_data` & `decoder_input_data` into `decoder_target_data`
    model = Model(inputs=encoder_inputs, outputs=decoder_outputs)
    
    # Compile the model
    model.compile(optimizer='adam', loss='mse')
    
    # Define sampling models
    encoder_model = Model(encoder_inputs, encoder_states)
    
    decoder_state_input_h = Input(shape=(lstm_units,))
    decoder_state_input_c = Input(shape=(lstm_units,))
    decoder_states_inputs = [decoder_state_input_h, decoder_state_input_c]
    
    decoder_outputs, state_h, state_c = decoder_lstm(decoder_inputs, initial_state=decoder_states_inputs)
    decoder_states = [state_h, state_c]
    decoder_outputs = decoder_dense(decoder_outputs)
    decoder_model = Model(
        [decoder_inputs] + decoder_states_inputs,
        [decoder_outputs] + decoder_states)
    
    return model, encoder_model, decoder_model


def create_shared_lstm_encoder_decoder(input_shape, n_ahead, flatten_output = False):
    sequence_length, n_features = input_shape
    
    # Input shape should be (sequence_length, n_features)
    encoder_inputs = Input(shape=input_shape)
    
    # Shared LSTM layer
    shared_lstm = LSTM(n_features, activation='tanh', return_sequences=True, return_state=True)
    
    # Encoder
    encoder_outputs, state_h, state_c = shared_lstm(encoder_inputs)
    encoder_states = [state_h, state_c]
    
    # Decoder
    decoder_inputs = RepeatVector(n_ahead)(state_h)
    decoder_outputs = shared_lstm(decoder_inputs, initial_state=encoder_states)[0]
    
    # Output layer
    decoder_dense = TimeDistributed(Dense(1))
    decoder_outputs = decoder_dense(decoder_outputs)

    if flatten_output:
        decoder_outputs = Flatten()(decoder_outputs)
    
    # Define the model
    model = Model(inputs=encoder_inputs, outputs=decoder_outputs)
    
    # Compile the model
    model.compile(optimizer='adam', loss='mse')
    
    # Sampling models for inference
    encoder_model = Model(encoder_inputs, encoder_states)
    
    decoder_state_input_h = Input(shape=(n_features,))
    decoder_state_input_c = Input(shape=(n_features,))
    decoder_states_inputs = [decoder_state_input_h, decoder_state_input_c]
    
    decoder_inputs = Input(shape=(1, n_features))
    decoder_outputs, state_h, state_c = shared_lstm(decoder_inputs, initial_state=decoder_states_inputs)
    decoder_states = [state_h, state_c]
    decoder_outputs = decoder_dense(decoder_outputs)
    decoder_model = Model(
        [decoder_inputs] + decoder_states_inputs,
        [decoder_outputs] + decoder_states)
    
    return model, encoder_model, decoder_model


# Model Comparison

In [26]:
def compare_models(
        generate: callable,
        models = [
            "Linear_Regression",
            "Ridge",
            "LSTM-Encoder-Decoder",
            "LSTM-Shared-Encoder-Decoder",
            "GRU-Last-Sequence",
            "GRU-Full-Sequence",
            'MLP-1-Layer-linear',
            'MLP-2-Layer-linear',
            'MLP-3-Layer-ReLU',
            "LinearNet",
            "LinearNet_no_convolution",
            "CLinear",
            "NLinear",
            "DLinear",
            "TSMixer-1",
            "TSMixer-2",
            "TSMixer_no_relu-1",
            "TSMixer_no_relu-2"
        ],
        sequence_lengths = [3, 10, 20, 50, 100, 200, 400],
        n_aheads = [1, 6, 15, 30, 90, 180, 360],
        n_run = 5, 
        display_summary = False, 
        exp_name = "",
    
    ):

    all_results = {seq_len: {model: {n_ahead: [] for n_ahead in n_aheads} for model in models} for seq_len in sequence_lengths}
    all_results_rmse = {seq_len: {model: {n_ahead: [] for n_ahead in n_aheads} for model in models} for seq_len in sequence_lengths}
    all_time_results = {seq_len: {model: {n_ahead: [] for n_ahead in n_aheads} for model in models} for seq_len in sequence_lengths}
    all_number_of_params = {seq_len: {model: {n_ahead: [] for n_ahead in n_aheads} for model in models} for seq_len in sequence_lengths}
    
    for sequence_length in sequence_lengths:
        for n_ahead in n_aheads:
            X_train, y_train, X_test, y_test = generate(sequence_length, n_ahead)
            
            for model_id in models:
                for run in range(n_run):
                    if model_id == "LSTM-Encoder-Decoder":
                        model, _, _ = create_lstm_encoder_decoder(X_train.shape[1:], n_ahead, lstm_units=50, flatten_output=True)
                    elif model_id == "LSTM-Shared-Encoder-Decoder":
                        model, _, _ = create_shared_lstm_encoder_decoder(X_train.shape[1:], n_ahead, flatten_output=True)
                    elif model_id == 'GRU-Last-Sequence':
                        model = keras.Sequential([
                            Input(shape=X_train.shape[1:]),
                            GRU(10, return_sequences=True),
                            GRU(10, return_sequences=False),
                            Dense(units=n_ahead, activation='linear')
                        ], name=model_id)
                    elif model_id == 'GRU-Full-Sequence':
                        model = keras.Sequential([
                            Input(shape=X_train.shape[1:]),
                            GRU(10, return_sequences=True),
                            GRU(10, return_sequences=True),
                            Flatten(),
                            Dense(units=n_ahead, activation='linear')
                        ], name=model_id)
                    elif model_id == 'MLP-1-Layer-linear':
                        model = keras.Sequential([
                            Input(shape=X_train.shape[1:]),
                            Flatten(),
                            Dense(n_ahead),
                        ], name=model_id)
                    elif model_id == 'MLP-2-Layer-linear':
                        model = keras.Sequential([
                            Input(shape=X_train.shape[1:]),
                            Flatten(),
                            Dense(n_ahead * 10 * 2),
                            Dense(n_ahead),
                        ], name=model_id)
                    elif model_id == 'MLP-3-Layer-ReLU':
                        model = keras.Sequential([
                            Input(shape=X_train.shape[1:]),
                            Flatten(),
                            Dense(n_ahead * 10 * 2, activation='relu'),
                            Dense(n_ahead * 10 * 2, activation='relu'),
                            Dense(n_ahead),
                        ], name=model_id)
                    elif model_id == 'LinearNet_no_convolution':
                        model = LinearNet(
                            output_len = n_ahead,
                            output_features = 1,
                            flatten_output = True,
                            hidden_layers = 2,
                            use_convolution = False,
                            name = model_id,
                        )
                        model.build(X_train.shape)
                    elif model_id == 'LinearNet':
                        model = LinearNet(
                            output_len = n_ahead,
                            output_features = 1,
                            flatten_output = True,
                            hidden_layers = 2,
                            use_convolution = True,
                            name = model_id,
                        )
                        model.build(X_train.shape)
                    elif model_id == "CLinear":
                        model = Sequential([
                            Input(shape=X_train.shape[1:]),
                            CLinear(n_ahead, individual = False),
                            Dense(1), #Needed as the models returns as many outputs as it has features, while here we sometime want to use many feature to 1 output
                            Flatten(),
                        ])
                    elif model_id == "NLinear":
                        model = Sequential([
                            Input(shape=X_train.shape[1:]),
                            NLinear(n_ahead, individual = False),
                            Dense(1), #Needed as the models returns as many outputs as it has features, while here we sometime want to use many feature to 1 output
                            Flatten(),
                        ])
                    elif model_id == "DLinear":
                        model = Sequential([
                            Input(shape=X_train.shape[1:]),
                            DLinear(n_ahead, individual = False),
                            Dense(1), #Needed as the models returns as many outputs as it has features, while here we sometime want to use many feature to 1 output
                            Flatten(),
                        ])
                    elif model_id == "TSMixer-1":
                        model = Sequential([
                            Input(shape=X_train.shape[1:]),
                            TSMixer(
                                input_shape = X_train.shape[1:],
                                pred_len = n_ahead,
                                norm_type = 'L',
                                activation = 'relu',
                                n_block = 1,
                                dropout = 0.,
                                ff_dim = 5,
                                target_slice = None,
                            ),
                            Dense(1), #Needed as the models returns as many outputs as it has features, while here we sometime want to use many feature to 1 output
                            Flatten(),
                        ])
                    elif model_id == "TSMixer-2":
                        model = Sequential([
                            Input(shape=X_train.shape[1:]),
                            TSMixer(
                                input_shape = X_train.shape[1:],
                                pred_len = n_ahead,
                                norm_type = 'L',
                                activation = 'relu',
                                n_block = 2,
                                dropout = 0.,
                                ff_dim = 5,
                                target_slice = None,
                            ),
                            Dense(1), #Needed as the models returns as many outputs as it has features, while here we sometime want to use many feature to 1 output
                            Flatten(),
                        ])
                    elif model_id == "TSMixer_no_relu-1":
                        model = Sequential([
                            Input(shape=X_train.shape[1:]),
                            TSMixer(
                                input_shape = X_train.shape[1:],
                                pred_len = n_ahead,
                                norm_type = 'L',
                                activation = 'linear',
                                n_block = 2,
                                dropout = 0.,
                                ff_dim = 5,
                                target_slice = None,
                            ),
                            Dense(1), #Needed as the models returns as many outputs as it has features, while here we sometime want to use many feature to 1 output
                            Flatten(),
                        ])
                    elif model_id == "TSMixer_no_relu-2":
                        model = Sequential([
                            Input(shape=X_train.shape[1:]),
                            TSMixer(
                                input_shape = X_train.shape[1:],
                                pred_len = n_ahead,
                                norm_type = 'L',
                                activation = 'linear',
                                n_block = 2,
                                dropout = 0.,
                                ff_dim = 5,
                                target_slice = None,
                            ),
                            Dense(1), #Needed as the models returns as many outputs as it has features, while here we sometime want to use many feature to 1 output
                            Flatten(),
                        ])
                    elif model_id == "Linear_Regression":
                        if run >0:
                            continue
                        if sequence_length >= 200:
                            continue
                        model = LinearRegression()
                        start_time = time.time()
                        X_train_flat = X_train.reshape(X_train.shape[0], -1)
                        X_test_flat = X_test.reshape(X_test.shape[0], -1)
                        y_train_flat = y_train.reshape(y_train.shape[0], -1)
                        y_test_flat = y_test.reshape(y_test.shape[0], -1)
                        model.fit(X_train_flat, y_train_flat)
                        end_time = time.time()
                        all_time_results[sequence_length][model_id][n_ahead].append(end_time - start_time)
                        # Evaluate the model on the test set
                        preds = model.predict(X_test_flat)
                        r2 = r2_score(y_true=y_test_flat, y_pred=preds)
                        rmse = root_mean_squared_error(y_true=y_test_flat, y_pred=preds)
                        all_results[sequence_length][model_id][n_ahead].append(r2)
                        all_results_rmse[sequence_length][model_id][n_ahead].append(rmse)
                        all_number_of_params[sequence_length][model_id][n_ahead].append((np.prod(X_train.shape[1:]) + 1) * n_ahead) 
                        print(f"Sequence Length: {sequence_length}, Model: {model_id}, N_ahead: {n_ahead}, Run: {run+1}, Time: {end_time - start_time:.2f}s, R2: {r2:.4f}")
                        del model
                        continue
                    elif model_id == "Ridge":
                        if run >0:
                            continue
                        if sequence_length >= 200:
                            continue
                        model = Ridge()
                        start_time = time.time()
                        X_train_flat = X_train.reshape(X_train.shape[0], -1)
                        X_test_flat = X_test.reshape(X_test.shape[0], -1)
                        y_train_flat = y_train.reshape(y_train.shape[0], -1)
                        y_test_flat = y_test.reshape(y_test.shape[0], -1)
                        model.fit(X_train_flat, y_train_flat)
                        end_time = time.time()
                        all_time_results[sequence_length][model_id][n_ahead].append(end_time - start_time)
                        # Evaluate the model on the test set
                        preds = model.predict(X_test_flat)
                        r2 = r2_score(y_true=y_test_flat, y_pred=preds)
                        rmse = root_mean_squared_error(y_true=y_test_flat, y_pred=preds)
                        all_results[sequence_length][model_id][n_ahead].append(r2)
                        all_results_rmse[sequence_length][model_id][n_ahead].append(rmse)
                        all_number_of_params[sequence_length][model_id][n_ahead].append((np.prod(X_train.shape[1:]) + 1) * n_ahead) 
                        print(f"Sequence Length: {sequence_length}, Model: {model_id}, N_ahead: {n_ahead}, Run: {run+1}, Time: {end_time - start_time:.2f}s, R2: {r2:.4f}")
                        del model
                        continue
                    else:
                        raise ValueError(f"Unknown model: {model_id}")
    
                    optimizer = keras.optimizers.Adam(0.001)
                    model.compile(optimizer=optimizer, loss='mean_squared_error', jit_compile=True)
                    if run == 0 and display_summary:
                        model.summary()
                    
                    start_time = time.time()
                    history = model.fit(X_train, y_train, batch_size=BATCH_SIZE, epochs=N_MAX_EPOCHS, validation_split=0.2, callbacks=callbacks(), shuffle=True, verbose=False)
                    end_time = time.time()
                    all_time_results[sequence_length][model_id][n_ahead].append(end_time - start_time)

                    preds = model.predict(X_test, batch_size=BATCH_SIZE, verbose=False)
                    r2 = r2_score(y_true=y_test, y_pred=preds)
                    rmse = root_mean_squared_error(y_true=y_test, y_pred=preds)
                    all_results[sequence_length][model_id][n_ahead].append(r2)
                    all_results_rmse[sequence_length][model_id][n_ahead].append(rmse)
                    all_number_of_params[sequence_length][model_id][n_ahead].append(model.count_params())
                    
                    print(f"Sequence Length: {sequence_length}, Model: {model_id}, N_ahead: {n_ahead}, Run: {run+1}, Time: {end_time - start_time:.2f}s, RMSE: {rmse:.4f}")
    
                    del model
                    del optimizer
                    keras.backend.clear_session()
    
    # Create multi-index DataFrames
    index = pd.MultiIndex.from_product([n_aheads, sequence_lengths], names=['n_ahead', 'sequence_length'])
    columns = pd.Index(models, name='model')
    
    df_r2 = pd.DataFrame(index=index, columns=columns)
    df_rmse = pd.DataFrame(index=index, columns=columns)
    df_time = pd.DataFrame(index=index, columns=columns)
    df_num_params = pd.DataFrame(index=index, columns=columns)

    df_r2_std = pd.DataFrame(index=index, columns=columns)
    df_rmse_std = pd.DataFrame(index=index, columns=columns)
    df_time_std = pd.DataFrame(index=index, columns=columns)
    
    for seq_len in sequence_lengths:
        for model in models:
            for n_ahead in n_aheads:
                df_r2.loc[(n_ahead, seq_len), model] = np.mean(all_results[seq_len][model][n_ahead])
                df_rmse.loc[(n_ahead, seq_len), model] = np.mean(all_results_rmse[seq_len][model][n_ahead])
                df_time.loc[(n_ahead, seq_len), model] = np.mean(all_time_results[seq_len][model][n_ahead])
                df_num_params.loc[(n_ahead, seq_len), model] = np.mean(all_number_of_params[seq_len][model][n_ahead])
                df_r2_std.loc[(n_ahead, seq_len), model] = np.std(all_results[seq_len][model][n_ahead])
                df_rmse_std.loc[(n_ahead, seq_len), model] = np.std(all_results_rmse[seq_len][model][n_ahead])
                df_time_std.loc[(n_ahead, seq_len), model] = np.std(all_time_results[seq_len][model][n_ahead])
    
    pd.set_option('display.max_rows', None)
    pd.set_option('display.max_columns', None)
    pd.set_option('display.width', None)
    pd.set_option('display.max_colwidth', None)
    print("R2 Scores Average:")
    display(df_r2)
    df_r2.to_parquet(f"{exp_name}_r2_avg.parquet")
    print("R2 Scores Std:")
    display(df_r2_std)
    df_r2_std.to_parquet(f"{exp_name}_r2_std.parquet")
    print("\nRMSE Scores Average:")
    display(df_rmse)
    df_rmse.to_parquet(f"{exp_name}_rmse_avg.parquet")
    print("\nRMSE Scores Std:")
    display(df_rmse_std)
    df_rmse_std.to_parquet(f"{exp_name}_rmse_std.parquet")
    print("\nTraining Times Average:")
    display(df_time)
    df_time.to_parquet(f"{exp_name}_time_avg.parquet")
    print("\nTraining Times Std:")
    display(df_time_std)
    df_time_std.to_parquet(f"{exp_name}_time_std.parquet")
    print("\nNumber of Parameters:")
    display(df_num_params)
    df_num_params.to_parquet(f"{exp_name}_num_params.parquet")
    pd.reset_option("display")

# ETTh1 Dataset

In [12]:

def get_hourly_dataset(path = 'ETDataset/ETT-small/ETTh1.csv', input_steps = 96, output_steps = 24, mode = "S", add_time_information=False):
    # Load the ETT dataset
    df = pd.read_csv(path)

    if add_time_information:
        df['date'] = pd.to_datetime(df['date'])
        df['hour'] = df['date'].apply(lambda x: x.hour)
        df['dayofweek'] = df['date'].apply(lambda x: x.dayofweek)
    
    # Assume 'OT' (oil temperature) is the target variable
    target_col = ['OT'] if "S" in mode else df.columns[1:]
    feature_cols = ['OT'] if mode=="S" else df.columns[1:]
    
    # Prepare the data
    X = df[feature_cols].values
    y = df[target_col].values
    
    border1s = [0, 12*30*24 - input_steps, 12*30*24+4*30*24 - input_steps]
    border2s = [12*30*24, 12*30*24+4*30*24, 12*30*24+8*30*24]
    
    # Split the data first
    X_train, X_test, y_train, y_test = X[border1s[0]:border2s[1]], X[border1s[1]:border2s[2]], y[border1s[0]:border2s[1]], y[border1s[1]:border2s[2]]
    
    # Initialize scalers
    scaler_X = StandardScaler()
    scaler_y = StandardScaler()
    
    # Fit and transform the training data
    X_train_scaled = scaler_X.fit_transform(X_train)
    y_train_scaled = scaler_y.fit_transform(y_train)
    
    # Transform the test data
    X_test_scaled = scaler_X.transform(X_test)
    y_test_scaled = scaler_y.transform(y_test)
    
    # Create sequences with multi-horizon outputs
    def create_sequences(X, y, input_steps, output_steps):
        Xs, ys = [], []
        for i in range(len(X) - input_steps - output_steps + 1):
            Xs.append(X[i:(i + input_steps)])
            ys.append(y[(i + input_steps):(i + input_steps + output_steps)])
        return np.array(Xs), np.array(ys)
    
    
    # Create sequences for training and test sets separately
    X_train_seq, y_train_seq = create_sequences(X_train_scaled, y_train_scaled, input_steps, output_steps)
    X_test_seq, y_test_seq = create_sequences(X_test_scaled, y_test_scaled, input_steps, output_steps)
    if "S" in mode:
        y_train_seq, y_test_seq = np.squeeze(y_train_seq), np.squeeze(y_test_seq)
    return X_train_seq, y_train_seq, X_test_seq, y_test_seq

## Univariate without time information

In [13]:
compare_models(
    generate = lambda sequence_length, n_ahead: get_hourly_dataset(input_steps = sequence_length, output_steps = n_ahead, mode = "S", add_time_information = False),
    exp_name="etth1_linearnet_results/etth1_univariate_without_time",
    n_run=1
)

Sequence Length: 3, Model: Linear_Regression, N_ahead: 1, Run: 1, Time: 0.00s, R2: 0.9869
Sequence Length: 3, Model: Ridge, N_ahead: 1, Run: 1, Time: 0.00s, R2: 0.9869
Sequence Length: 3, Model: LSTM-Encoder-Decoder, N_ahead: 1, Run: 1, Time: 6.72s, RMSE: 0.0952
Sequence Length: 3, Model: LSTM-Shared-Encoder-Decoder, N_ahead: 1, Run: 1, Time: 7.52s, RMSE: 0.1843
Sequence Length: 3, Model: GRU-Last-Sequence, N_ahead: 1, Run: 1, Time: 7.72s, RMSE: 0.0966
Sequence Length: 3, Model: GRU-Full-Sequence, N_ahead: 1, Run: 1, Time: 7.67s, RMSE: 0.0946
Sequence Length: 3, Model: MLP-1-Layer-linear, N_ahead: 1, Run: 1, Time: 9.49s, RMSE: 0.0937
Sequence Length: 3, Model: MLP-2-Layer-linear, N_ahead: 1, Run: 1, Time: 5.20s, RMSE: 0.0938
Sequence Length: 3, Model: MLP-3-Layer-ReLU, N_ahead: 1, Run: 1, Time: 5.51s, RMSE: 0.0937
Sequence Length: 3, Model: LinearNet, N_ahead: 1, Run: 1, Time: 9.41s, RMSE: 0.0934
Sequence Length: 3, Model: LinearNet_no_convolution, N_ahead: 1, Run: 1, Time: 10.87s, RMS

/usr/local/lib/python3.10/dist-packages/numpy/core/fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:129: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:206: RuntimeWarning: Degrees of freedom <= 0 for slice
  ret = _var(a, axis=axis, dtype=dtype, out=out, ddof=ddof,
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:163: RuntimeWarning: invalid value encountered in divide
  arrmean = um.true_divide(arrmean, div, out=arrmean,
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:198: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)


model                   Linear_Regression     Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                    
1       3                        0.986882  0.986882             0.986267   
        10                       0.986958  0.986959             0.986708   
        20                       0.987296  0.987297             0.986949   
        50                        0.98776   0.98776             0.986803   
        100                       0.98807   0.98807             0.987075   
        200                           NaN       NaN             0.987005   
        400                           NaN       NaN             0.987477   
6       3                        0.957609  0.957614               0.9556   
        10                       0.959379  0.959386             0.955446   
        20                       0.962942  0.962948             0.958683   
        50                       0.965761  0.965766             0.957495   
        100                      0.967693  0.967698             0.963838   
        200                           NaN       NaN             0.959654   
        400                           NaN       NaN             0.960365   
15      3                        0.920549  0.920549             0.899566   
        10                       0.930547  0.930553             0.907581   
        20                       0.935365   0.93537             0.915848   
        50                       0.939948  0.939952             0.903365   
        100                      0.943961  0.943965             0.912838   
        200                           NaN       NaN             0.917425   
        400                           NaN       NaN              0.92807   
30      3                        0.894877  0.894875             0.833604   
        10                       0.903147   0.90315             0.855405   
        20                       0.907264  0.907268             0.844867   
        50                       0.913981  0.913984             0.789805   
        100                      0.918951  0.918955             0.874629   
        200                           NaN       NaN             0.872261   
        400                           NaN       NaN             0.813659   
90      3                        0.809389  0.809382               0.5742   
        10                       0.825247  0.825245             0.652324   
        20                        0.83427  0.834271              0.66492   
        50                       0.850011  0.850012             0.660031   
        100                      0.861291  0.861293             0.669872   
        200                           NaN       NaN             0.638691   
        400                           NaN       NaN             0.660734   
180     3                        0.760527  0.760517             0.526676   
        10                       0.778734   0.77873             0.558277   
        20                       0.790792  0.790792             0.549136   
        50                       0.811409  0.811409             0.628916   
        100                      0.826465  0.826466             0.562883   
        200                           NaN       NaN             0.661375   
        400                           NaN       NaN             0.653558   
360     3                        0.706492  0.706479             0.505191   
        10                       0.726926   0.72692             0.485314   
        20                       0.740398  0.740396             0.515634   
        50                       0.764927  0.764926             0.578504   
        100                      0.783546  0.783546             0.572693   
        200                           NaN       NaN              0.57223   
        400                           NaN       NaN              0.56381   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                           

R2 Scores Std:


model                   Linear_Regression Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                
1       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
6       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
15      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
30      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
90      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
180     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
360     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                                                 
1       3                                       0.0               0.0   
        10                                      0.0               0.0   
        20                         

...

model                   Linear_Regression     Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                    
1       3                        0.001421  0.001469             6.716093   
        10                        0.00393  0.002041              7.89165   
        20                       0.006098  0.002291             9.431497   
        50                       0.017162  0.005281            14.628092   
        100                      0.035094  0.011575            21.874898   
        200                           NaN       NaN            37.040497   
        400                           NaN       NaN            62.494367   
6       3                        0.005815  0.001818             8.651334   
        10                       0.004712  0.002277            10.243893   
        20                       0.008063  0.002503            12.476442   
        50                        0.01822  0.005753            13.445309   
        100                      0.037767  0.077378            16.093386   
        200                           NaN       NaN            27.320385   
        400                           NaN       NaN            43.555567   
15      3                        0.005982  0.002379             8.223967   
        10                       0.007185  0.002613             7.928564   
        20                       0.010833  0.003719            10.042608   
        50                       0.020816  0.007029            10.456338   
        100                      0.042932  0.011017            15.464793   
        200                           NaN       NaN            23.582645   
        400                           NaN       NaN             50.86638   
30      3                        0.009041  0.002442             7.750999   
        10                       0.009307  0.003231            12.854705   
        20                       0.015521  0.004886            13.443431   
        50                       0.025677  0.041775            18.094072   
        100                      0.045984  0.027991            19.405483   
        200                           NaN       NaN            24.981852   
        400                           NaN       NaN            26.977602   
90      3                        0.020086  0.007366            12.199281   
        10                       0.014384   0.00676            20.267908   
        20                       0.016472  0.188141            13.828829   
        50                       0.032276  0.106922            20.820739   
        100                      0.057177  0.098122            20.710547   
        200                           NaN       NaN            30.083812   
        400                           NaN       NaN            44.520525   
180     3                        0.028656  0.013383            19.167678   
        10                       0.028249   0.15389            23.121156   
        20                       0.028179   0.10229            18.234622   
        50                       0.046065  0.100456            25.249275   
        100                      0.082051  0.029003            28.450933   
        200                           NaN       NaN            30.520911   
        400                           NaN       NaN            47.391941   
360     3                        0.056294  0.024814            28.320818   
        10                       0.056905  0.093836            26.964348   
        20                       0.069909   0.02545            65.906198   
        50                        0.20402   0.19456            29.787009   
        100                      0.238297  0.170834            36.363899   
        200                           NaN       NaN            50.249797   
        400                           NaN       NaN            43.262012   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                           


Training Times Std:


model                   Linear_Regression Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                
1       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
6       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
15      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
30      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
90      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
180     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
360     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                                                 
1       3                                       0.0               0.0   
        10                                      0.0               0.0   
        20                         


Number of Parameters:


model                   Linear_Regression    Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                   
1       3                             4.0      4.0              30651.0   
        10                           11.0     11.0              30651.0   
        20                           21.0     21.0              30651.0   
        50                           51.0     51.0              30651.0   
        100                         101.0    101.0              30651.0   
        200                           NaN      NaN              30651.0   
        400                           NaN      NaN              30651.0   
6       3                            24.0     24.0              30651.0   
        10                           66.0     66.0              30651.0   
        20                          126.0    126.0              30651.0   
        50                          306.0    306.0              30651.0   
        100                         606.0    606.0              30651.0   
        200                           NaN      NaN              30651.0   
        400                           NaN      NaN              30651.0   
15      3                            60.0     60.0              30651.0   
        10                          165.0    165.0              30651.0   
        20                          315.0    315.0              30651.0   
        50                          765.0    765.0              30651.0   
        100                        1515.0   1515.0              30651.0   
        200                           NaN      NaN              30651.0   
        400                           NaN      NaN              30651.0   
30      3                           120.0    120.0              30651.0   
        10                          330.0    330.0              30651.0   
        20                          630.0    630.0              30651.0   
        50                         1530.0   1530.0              30651.0   
        100                        3030.0   3030.0              30651.0   
        200                           NaN      NaN              30651.0   
        400                           NaN      NaN              30651.0   
90      3                           360.0    360.0              30651.0   
        10                          990.0    990.0              30651.0   
        20                         1890.0   1890.0              30651.0   
        50                         4590.0   4590.0              30651.0   
        100                        9090.0   9090.0              30651.0   
        200                           NaN      NaN              30651.0   
        400                           NaN      NaN              30651.0   
180     3                           720.0    720.0              30651.0   
        10                         1980.0   1980.0              30651.0   
        20                         3780.0   3780.0              30651.0   
        50                         9180.0   9180.0              30651.0   
        100                       18180.0  18180.0              30651.0   
        200                           NaN      NaN              30651.0   
        400                           NaN      NaN              30651.0   
360     3                          1440.0   1440.0              30651.0   
        10                         3960.0   3960.0              30651.0   
        20                         7560.0   7560.0              30651.0   
        50                        18360.0  18360.0              30651.0   
        100                       36360.0  36360.0              30651.0   
        200                           NaN      NaN              30651.0   
        400                           NaN      NaN              30651.0   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                                                 
1       3                   

## Univariate + time information (so multivariate but with only OT info from datas)

In [ ]:
compare_models(
    generate = lambda sequence_length, n_ahead: get_hourly_dataset(input_steps = sequence_length, output_steps = n_ahead, mode = "S", add_time_information = True),
    exp_name="etth1_linearnet_results/etth1_univariate_with_time",
    n_run=1
)

Sequence Length: 3, Model: Linear_Regression, N_ahead: 1, Run: 1, Time: 0.00s, R2: 0.9869
Sequence Length: 3, Model: Ridge, N_ahead: 1, Run: 1, Time: 0.00s, R2: 0.9869
Sequence Length: 3, Model: LSTM-Encoder-Decoder, N_ahead: 1, Run: 1, Time: 7.11s, RMSE: 0.0928
Sequence Length: 3, Model: LSTM-Shared-Encoder-Decoder, N_ahead: 1, Run: 1, Time: 8.52s, RMSE: 0.1460
Sequence Length: 3, Model: GRU-Last-Sequence, N_ahead: 1, Run: 1, Time: 7.18s, RMSE: 0.0964
Sequence Length: 3, Model: GRU-Full-Sequence, N_ahead: 1, Run: 1, Time: 7.25s, RMSE: 0.0949
Sequence Length: 3, Model: MLP-1-Layer-linear, N_ahead: 1, Run: 1, Time: 7.68s, RMSE: 0.0934
Sequence Length: 3, Model: MLP-2-Layer-linear, N_ahead: 1, Run: 1, Time: 3.27s, RMSE: 0.0934
Sequence Length: 3, Model: MLP-3-Layer-ReLU, N_ahead: 1, Run: 1, Time: 4.62s, RMSE: 0.0940
Sequence Length: 3, Model: LinearNet, N_ahead: 1, Run: 1, Time: 5.89s, RMSE: 0.0932
Sequence Length: 3, Model: LinearNet_no_convolution, N_ahead: 1, Run: 1, Time: 5.17s, RMSE

## Multivariate without time information

In [15]:
compare_models(
    generate = lambda sequence_length, n_ahead: get_hourly_dataset(input_steps = sequence_length, output_steps = n_ahead, mode = "MS", add_time_information = False),
    exp_name="etth1_linearnet_results/etth1_multivariate_without_time",
    n_run=1
)

Sequence Length: 3, Model: GRU-Full-Sequence, N_ahead: 1, Run: 1, Time: 49.41s, RMSE: 0.1259
Sequence Length: 3, Model: MLP-1-Layer-linear, N_ahead: 1, Run: 1, Time: 4.37s, RMSE: 0.1289
Sequence Length: 3, Model: MLP-2-Layer-linear, N_ahead: 1, Run: 1, Time: 4.34s, RMSE: 0.0977
Sequence Length: 3, Model: MLP-3-Layer-ReLU, N_ahead: 1, Run: 1, Time: 6.01s, RMSE: 0.1157
Sequence Length: 3, Model: LinearNet, N_ahead: 1, Run: 1, Time: 19.45s, RMSE: 0.1020
Sequence Length: 3, Model: LinearNet_no_convolution, N_ahead: 1, Run: 1, Time: 8.02s, RMSE: 0.0976
Sequence Length: 3, Model: CLinear, N_ahead: 1, Run: 1, Time: 22.15s, RMSE: 0.1021
Sequence Length: 3, Model: NLinear, N_ahead: 1, Run: 1, Time: 9.36s, RMSE: 0.1051
Sequence Length: 3, Model: DLinear, N_ahead: 1, Run: 1, Time: 5.77s, RMSE: 0.0960
Sequence Length: 3, Model: TSMixer-1, N_ahead: 1, Run: 1, Time: 13.61s, RMSE: 0.0964
Sequence Length: 3, Model: TSMixer-2, N_ahead: 1, Run: 1, Time: 13.50s, RMSE: 0.2038
Sequence Length: 3, Model: TS

/usr/local/lib/python3.10/dist-packages/numpy/core/fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:129: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:206: RuntimeWarning: Degrees of freedom <= 0 for slice
  ret = _var(a, axis=axis, dtype=dtype, out=out, ddof=ddof,
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:163: RuntimeWarning: invalid value encountered in divide
  arrmean = um.true_divide(arrmean, div, out=arrmean,
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:198: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)


model                   Linear_Regression     Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                    
1       3                        0.986817  0.986812             0.983567   
        10                       0.987229  0.987225             0.981156   
        20                       0.987763  0.987766             0.981309   
        50                       0.987959  0.987966             0.978379   
        100                      0.988103  0.988121             0.982728   
        200                           NaN       NaN             0.984178   
        400                           NaN       NaN              0.97604   
6       3                         0.95548  0.955469             0.936206   
        10                       0.960673  0.960667              0.93258   
        20                       0.965562   0.96557              0.94411   
        50                       0.967058  0.967072             0.918008   
        100                      0.968415  0.968447             0.939183   
        200                           NaN       NaN             0.936616   
        400                           NaN       NaN             0.936016   
15      3                        0.914147   0.91412             0.858062   
        10                       0.932227  0.932219             0.855999   
        20                         0.9378   0.93781             0.861574   
        50                       0.940923  0.940937              0.84635   
        100                      0.944357  0.944394             0.839635   
        200                           NaN       NaN             0.802029   
        400                           NaN       NaN             0.850723   
30      3                        0.888185   0.88816             0.816992   
        10                       0.902516  0.902506             0.768312   
        20                       0.908336  0.908345             0.729106   
        50                       0.915292  0.915312             0.690052   
        100                      0.920065  0.920108             0.710236   
        200                           NaN       NaN             0.705319   
        400                           NaN       NaN             0.699802   
90      3                        0.792498  0.792473             0.536202   
        10                       0.821811  0.821804             0.412566   
        20                       0.836353  0.836376             0.370002   
        50                       0.855547  0.855587             0.294404   
        100                      0.861395  0.861473             0.176468   
        200                           NaN       NaN             0.345829   
        400                           NaN       NaN             0.446425   
180     3                        0.753085  0.753078             0.368169   
        10                       0.786694  0.786708             0.232159   
        20                       0.803451  0.803504             0.227286   
        50                       0.818008   0.81809             0.266779   
        100                      0.814352  0.814472            -0.137127   
        200                           NaN       NaN            -0.256025   
        400                           NaN       NaN             0.133126   
360     3                        0.714791  0.714786             0.327108   
        10                       0.748154  0.748181             0.149491   
        20                        0.76255  0.762613             0.074391   
        50                       0.774716  0.774802            -0.149062   
        100                      0.775045  0.775163            -0.325061   
        200                           NaN       NaN            -0.328495   
        400                           NaN       NaN            -0.189687   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                           

R2 Scores Std:


model                   Linear_Regression Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                
1       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
6       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
15      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
30      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
90      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
180     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
360     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                                                 
1       3                                       0.0               0.0   
        10                                      0.0               0.0   
        20                         

...

model                   Linear_Regression     Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                    
1       3                        0.007625  0.003216             7.588093   
        10                       0.026222  0.007341             7.447889   
        20                        0.10408  0.099777              7.60827   
        50                       0.593839  0.102394             9.822002   
        100                      1.742544  0.297015            12.875798   
        200                           NaN       NaN            28.081408   
        400                           NaN       NaN            28.364158   
6       3                        0.008895  0.003713             6.682925   
        10                       0.025696  0.008126             7.147105   
        20                       0.083426  0.114826             7.430992   
        50                       0.443284  0.206961            10.035765   
        100                      2.435708  0.262813            12.224029   
        200                           NaN       NaN            17.709826   
        400                           NaN       NaN            30.453423   
15      3                        0.013615  0.004616             6.935637   
        10                       0.032553  0.009425             7.327867   
        20                       0.082527    0.0998             8.456744   
        50                       0.517744  0.134799            10.867402   
        100                      2.355991  0.301135               12.978   
        200                           NaN       NaN            17.583972   
        400                           NaN       NaN            30.638143   
30      3                        0.018989   0.00493              7.56905   
        10                       0.030965  0.025553             8.617508   
        20                       0.141982  0.034603             9.003062   
        50                       0.724713  0.141313            10.414433   
        100                      2.055336  0.321233            13.358751   
        200                           NaN       NaN            18.499739   
        400                           NaN       NaN            32.371794   
90      3                        0.018557    0.1218             11.04693   
        10                       0.129581  0.101168            11.395759   
        20                       0.124975  0.184811             12.16715   
        50                       0.863639  0.126535            13.496767   
        100                      2.277625  0.297864            17.154407   
        200                           NaN       NaN            21.534035   
        400                           NaN       NaN            35.553248   
180     3                        0.031768  0.148315            17.495002   
        10                       0.069537  0.028049            18.099165   
        20                       0.299287  0.107254            18.415953   
        50                       1.011097  0.374496            20.712545   
        100                      2.847343  0.302406            22.075325   
        200                           NaN       NaN            26.363273   
        400                           NaN       NaN             38.84129   
360     3                         0.06744  0.017958            25.843081   
        10                       0.264797  0.119335            26.130444   
        20                        0.38243  0.103523            47.030466   
        50                       1.228807  0.208707            64.591209   
        100                      3.038917  0.375481            43.594446   
        200                           NaN       NaN            35.425225   
        400                           NaN       NaN            44.511607   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                           


Training Times Std:


model                   Linear_Regression Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                
1       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
6       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
15      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
30      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
90      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
180     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
360     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                                                 
1       3                                       0.0               0.0   
        10                                      0.0               0.0   
        20                         


Number of Parameters:


model                   Linear_Regression     Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                    
1       3                            22.0      22.0              31851.0   
        10                           71.0      71.0              31851.0   
        20                          141.0     141.0              31851.0   
        50                          351.0     351.0              31851.0   
        100                         701.0     701.0              31851.0   
        200                           NaN       NaN              31851.0   
        400                           NaN       NaN              31851.0   
6       3                           132.0     132.0              31851.0   
        10                          426.0     426.0              31851.0   
        20                          846.0     846.0              31851.0   
        50                         2106.0    2106.0              31851.0   
        100                        4206.0    4206.0              31851.0   
        200                           NaN       NaN              31851.0   
        400                           NaN       NaN              31851.0   
15      3                           330.0     330.0              31851.0   
        10                         1065.0    1065.0              31851.0   
        20                         2115.0    2115.0              31851.0   
        50                         5265.0    5265.0              31851.0   
        100                       10515.0   10515.0              31851.0   
        200                           NaN       NaN              31851.0   
        400                           NaN       NaN              31851.0   
30      3                           660.0     660.0              31851.0   
        10                         2130.0    2130.0              31851.0   
        20                         4230.0    4230.0              31851.0   
        50                        10530.0   10530.0              31851.0   
        100                       21030.0   21030.0              31851.0   
        200                           NaN       NaN              31851.0   
        400                           NaN       NaN              31851.0   
90      3                          1980.0    1980.0              31851.0   
        10                         6390.0    6390.0              31851.0   
        20                        12690.0   12690.0              31851.0   
        50                        31590.0   31590.0              31851.0   
        100                       63090.0   63090.0              31851.0   
        200                           NaN       NaN              31851.0   
        400                           NaN       NaN              31851.0   
180     3                          3960.0    3960.0              31851.0   
        10                        12780.0   12780.0              31851.0   
        20                        25380.0   25380.0              31851.0   
        50                        63180.0   63180.0              31851.0   
        100                      126180.0  126180.0              31851.0   
        200                           NaN       NaN              31851.0   
        400                           NaN       NaN              31851.0   
360     3                          7920.0    7920.0              31851.0   
        10                        25560.0   25560.0              31851.0   
        20                        50760.0   50760.0              31851.0   
        50                       126360.0  126360.0              31851.0   
        100                      252360.0  252360.0              31851.0   
        200                           NaN       NaN              31851.0   
        400                           NaN       NaN              31851.0   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                           

## Multivariate with time information

In [16]:
compare_models(
    generate = lambda sequence_length, n_ahead: get_hourly_dataset(input_steps = sequence_length, output_steps = n_ahead, mode = "MS", add_time_information = True),
    exp_name="etth1_linearnet_results/etth1_multivariate_with_time",
    n_run=1
)

Sequence Length: 3, Model: Linear_Regression, N_ahead: 1, Run: 1, Time: 0.01s, R2: 0.9870
Sequence Length: 3, Model: Ridge, N_ahead: 1, Run: 1, Time: 0.00s, R2: 0.9870
Sequence Length: 3, Model: LSTM-Encoder-Decoder, N_ahead: 1, Run: 1, Time: 6.88s, RMSE: 0.1027
Sequence Length: 3, Model: LSTM-Shared-Encoder-Decoder, N_ahead: 1, Run: 1, Time: 10.13s, RMSE: 0.1127
Sequence Length: 3, Model: GRU-Last-Sequence, N_ahead: 1, Run: 1, Time: 9.09s, RMSE: 0.1289
Sequence Length: 3, Model: GRU-Full-Sequence, N_ahead: 1, Run: 1, Time: 6.89s, RMSE: 0.1065
Sequence Length: 3, Model: MLP-1-Layer-linear, N_ahead: 1, Run: 1, Time: 6.68s, RMSE: 0.0959
Sequence Length: 3, Model: MLP-2-Layer-linear, N_ahead: 1, Run: 1, Time: 3.74s, RMSE: 0.1000
Sequence Length: 3, Model: MLP-3-Layer-ReLU, N_ahead: 1, Run: 1, Time: 5.51s, RMSE: 0.1081
Sequence Length: 3, Model: LinearNet, N_ahead: 1, Run: 1, Time: 8.16s, RMSE: 0.0960
Sequence Length: 3, Model: LinearNet_no_convolution, N_ahead: 1, Run: 1, Time: 7.51s, RMS

/usr/local/lib/python3.10/dist-packages/numpy/core/fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:129: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:206: RuntimeWarning: Degrees of freedom <= 0 for slice
  ret = _var(a, axis=axis, dtype=dtype, out=out, ddof=ddof,
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:163: RuntimeWarning: invalid value encountered in divide
  arrmean = um.true_divide(arrmean, div, out=arrmean,
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:198: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)


model                   Linear_Regression     Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                    
1       3                        0.986963  0.986959              0.98404   
        10                       0.987532  0.987529             0.980554   
        20                       0.987956  0.987959             0.983249   
        50                       0.988042  0.988049             0.971463   
        100                      0.988061   0.98808             0.975548   
        200                           NaN       NaN              0.97742   
        400                           NaN       NaN              0.98069   
6       3                         0.95875  0.958744             0.944797   
        10                       0.963929  0.963926             0.946907   
        20                       0.966915  0.966919             0.925144   
        50                       0.968036  0.968046             0.925642   
        100                      0.968698  0.968734             0.937203   
        200                           NaN       NaN             0.943299   
        400                           NaN       NaN             0.917291   
15      3                         0.92435  0.924335             0.871836   
        10                       0.936171  0.936167             0.872734   
        20                       0.940222  0.940227             0.850568   
        50                       0.943155  0.943171             0.850985   
        100                      0.944713  0.944758             0.855067   
        200                           NaN       NaN             0.842315   
        400                           NaN       NaN             0.853247   
30      3                        0.894069   0.89405             0.798828   
        10                       0.905604  0.905598              0.75966   
        20                       0.909566  0.909572             0.683695   
        50                       0.915768  0.915784              0.62584   
        100                      0.917849  0.917888             0.718149   
        200                           NaN       NaN             0.729252   
        400                           NaN       NaN              0.71927   
90      3                         0.80004   0.80002             0.505168   
        10                       0.821643  0.821639             0.406793   
        20                       0.833162  0.833182             0.436778   
        50                       0.851983   0.85201             0.247828   
        100                      0.856301  0.856387             0.082717   
        200                           NaN       NaN              0.26545   
        400                           NaN       NaN              0.34686   
180     3                        0.761739  0.761735             0.313849   
        10                       0.786884  0.786901             0.127244   
        20                       0.800755  0.800805             0.140812   
        50                       0.815771  0.815853            -0.075772   
        100                      0.810368  0.810491             0.268093   
        200                           NaN       NaN             0.074231   
        400                           NaN       NaN            -0.181833   
360     3                        0.723095  0.723097             0.297692   
        10                       0.747546  0.747576             0.179382   
        20                       0.760212  0.760274             0.062353   
        50                       0.772738  0.772879            -0.088092   
        100                       0.77188  0.771994              0.01704   
        200                           NaN       NaN            -0.168428   
        400                           NaN       NaN            -0.083769   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                           

R2 Scores Std:


model                   Linear_Regression Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                
1       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
6       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
15      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
30      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
90      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
180     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
360     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                                                 
1       3                                       0.0               0.0   
        10                                      0.0               0.0   
        20                         

...

model                   Linear_Regression     Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                    
1       3                        0.007429  0.002856             6.882465   
        10                       0.028538  0.009319              7.36471   
        20                       0.102458  0.091379            10.257537   
        50                       0.798203  0.207158            17.129926   
        100                      3.039722  0.387366            18.478477   
        200                           NaN       NaN            27.109843   
        400                           NaN       NaN            49.667397   
6       3                        0.011076  0.003912             7.477755   
        10                       0.035314  0.011595             7.736869   
        20                         0.1098  0.179145             7.406044   
        50                       0.948822  0.209355             9.905996   
        100                       2.72676  0.384276            12.695089   
        200                           NaN       NaN            17.623812   
        400                           NaN       NaN            29.752645   
15      3                        0.015331  0.004534             6.895027   
        10                       0.029722  0.008978             7.414604   
        20                       0.073799  0.106682             8.579631   
        50                       1.061599   0.20919             11.13607   
        100                      3.992095  0.372196            14.222209   
        200                           NaN       NaN            19.237258   
        400                           NaN       NaN            27.621506   
30      3                        0.018971  0.004505              7.74036   
        10                       0.036523   0.05633             8.053186   
        20                       0.152026  0.187914             9.397389   
        50                       0.936842  0.160807            11.674234   
        100                      3.879091  0.372091            13.815251   
        200                           NaN       NaN            18.636493   
        400                           NaN       NaN            30.122094   
90      3                        0.018701  0.033382            11.618958   
        10                       0.047435  0.135072            12.197964   
        20                       0.160877  0.107542            12.938847   
        50                       1.373549  0.165073            14.344424   
        100                      3.722557  0.497712            16.765401   
        200                           NaN       NaN            21.615302   
        400                           NaN       NaN            31.180642   
180     3                        0.034489    0.1905            19.815949   
        10                         0.0641  0.190126            17.181294   
        20                       0.202679   0.11917            20.579954   
        50                       1.313591  0.173432            20.961132   
        100                      3.140724  0.397268            21.761383   
        200                           NaN       NaN             31.47218   
        400                           NaN       NaN            37.437155   
360     3                        0.073477  0.091854            30.814879   
        10                       0.121531   0.10974            26.675245   
        20                       0.402853  0.104554            29.301327   
        50                       1.883789  0.095546            32.471637   
        100                      3.872788  0.293669           211.047228   
        200                           NaN       NaN            39.257553   
        400                           NaN       NaN              44.8942   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                           


Training Times Std:


model                   Linear_Regression Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                
1       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
6       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
15      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
30      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
90      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
180     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
360     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                                                 
1       3                                       0.0               0.0   
        10                                      0.0               0.0   
        20                         


Number of Parameters:


model                   Linear_Regression     Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                    
1       3                            28.0      28.0              32251.0   
        10                           91.0      91.0              32251.0   
        20                          181.0     181.0              32251.0   
        50                          451.0     451.0              32251.0   
        100                         901.0     901.0              32251.0   
        200                           NaN       NaN              32251.0   
        400                           NaN       NaN              32251.0   
6       3                           168.0     168.0              32251.0   
        10                          546.0     546.0              32251.0   
        20                         1086.0    1086.0              32251.0   
        50                         2706.0    2706.0              32251.0   
        100                        5406.0    5406.0              32251.0   
        200                           NaN       NaN              32251.0   
        400                           NaN       NaN              32251.0   
15      3                           420.0     420.0              32251.0   
        10                         1365.0    1365.0              32251.0   
        20                         2715.0    2715.0              32251.0   
        50                         6765.0    6765.0              32251.0   
        100                       13515.0   13515.0              32251.0   
        200                           NaN       NaN              32251.0   
        400                           NaN       NaN              32251.0   
30      3                           840.0     840.0              32251.0   
        10                         2730.0    2730.0              32251.0   
        20                         5430.0    5430.0              32251.0   
        50                        13530.0   13530.0              32251.0   
        100                       27030.0   27030.0              32251.0   
        200                           NaN       NaN              32251.0   
        400                           NaN       NaN              32251.0   
90      3                          2520.0    2520.0              32251.0   
        10                         8190.0    8190.0              32251.0   
        20                        16290.0   16290.0              32251.0   
        50                        40590.0   40590.0              32251.0   
        100                       81090.0   81090.0              32251.0   
        200                           NaN       NaN              32251.0   
        400                           NaN       NaN              32251.0   
180     3                          5040.0    5040.0              32251.0   
        10                        16380.0   16380.0              32251.0   
        20                        32580.0   32580.0              32251.0   
        50                        81180.0   81180.0              32251.0   
        100                      162180.0  162180.0              32251.0   
        200                           NaN       NaN              32251.0   
        400                           NaN       NaN              32251.0   
360     3                         10080.0   10080.0              32251.0   
        10                        32760.0   32760.0              32251.0   
        20                        65160.0   65160.0              32251.0   
        50                       162360.0  162360.0              32251.0   
        100                      324360.0  324360.0              32251.0   
        200                           NaN       NaN              32251.0   
        400                           NaN       NaN              32251.0   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                           

# BTC Notional

In [27]:
class MinMaxScaler:
    def __init__(self, feature_axis=None, minmax_range=(0, 1)):
        """
        Initialize the MinMaxScaler.
        Args:
        feature_axis (int, optional): The axis that represents the feature dimension if applicable.
                                      Use only for 3D data to specify which axis is the feature axis.
                                      Default is None, automatically managed based on data dimensions.
        """
        self.feature_axis = feature_axis
        self.min_ = None
        self.max_ = None
        self.scale_ = None
        self.minmax_range = minmax_range # Default range for scaling (min, max)

    def fit(self, X):
        """
        Fit the scaler to the data based on its dimensionality.
        Args:
        X (np.array): The data to fit the scaler on.
        """
        if X.ndim == 3 and self.feature_axis is not None:  # 3D data
            axis = tuple(i for i in range(X.ndim) if i != self.feature_axis)
            self.min_ = np.min(X, axis=axis)
            self.max_ = np.max(X, axis=axis)
        elif X.ndim == 2:  # 2D data
            self.min_ = np.min(X, axis=0)
            self.max_ = np.max(X, axis=0)
        elif X.ndim == 1:  # 1D data
            self.min_ = np.min(X)
            self.max_ = np.max(X)
        else:
            raise ValueError("Data must be 1D, 2D, or 3D.")

        self.scale_ = self.max_ - self.min_
        return self

    def transform(self, X):
        """
        Transform the data using the fitted scaler.
        Args:
        X (np.array): The data to transform.
        Returns:
        np.array: The scaled data.
        """
        X_scaled = (X - self.min_) / self.scale_
        X_scaled = X_scaled * (self.minmax_range[1] - self.minmax_range[0]) + self.minmax_range[0]
        return X_scaled

    def fit_transform(self, X):
        """
        Fit to data, then transform it.
        Args:
        X (np.array): The data to fit and transform.
        Returns:
        np.array: The scaled data.
        """
        return self.fit(X).transform(X)

    def inverse_transform(self, X_scaled):
        """
        Inverse transform the scaled data to original data.
        Args:
        X_scaled (np.array): The scaled data to inverse transform.
        Returns:
        np.array: The original data scale.
        """
        X = (X_scaled - self.minmax_range[0]) / (self.minmax_range[1] - self.minmax_range[0])
        X = X * self.scale_ + self.min_
        return X

def generate_data(df, sequence_length, n_ahead = 1):
    #Case without known inputs
    scaler_df = df.copy().shift(n_ahead).rolling(24 * 14).median()
    tmp_df = df.copy() / scaler_df
    tmp_df = tmp_df.iloc[24 * 14 + n_ahead:].fillna(0.)
    scaler_df = scaler_df.iloc[24 * 14 + n_ahead:].fillna(0.)
    def prepare_sequences(df, scaler_df, n_history, n_future):
        X, y, y_scaler = [], [], []
        num_features = df.shape[1]
        
        # Iterate through the DataFrame to create sequences
        for i in range(n_history, len(df) - n_future + 1):
            # Extract the sequence of past observations
            X.append(df.iloc[i - n_history:i].values)
            # Extract the future values of the first column
            y.append(df.iloc[i:i + n_future,0:1].values)
            y_scaler.append(scaler_df.iloc[i:i + n_future,0:1].values)
        
        X, y, y_scaler = np.array(X), np.array(y), np.array(y_scaler)
        return X, y, y_scaler
    
    # Prepare sequences
    X, y, y_scaler = prepare_sequences(tmp_df, scaler_df, sequence_length, n_ahead)
    
    # Split the dataset into training and testing sets
    train_test_separation = int(len(X) * 0.8)
    X_train_unscaled, X_test_unscaled = X[:train_test_separation], X[train_test_separation:]
    y_train_unscaled, y_test_unscaled = y[:train_test_separation], y[train_test_separation:]
    y_scaler_train, y_scaler_test = y_scaler[:train_test_separation], y_scaler[train_test_separation:]
    
    # Generate the data
    X_scaler = MinMaxScaler(feature_axis=2)
    X_train = X_scaler.fit_transform(X_train_unscaled)
    X_test = X_scaler.transform(X_test_unscaled)
    
    y_scaler = MinMaxScaler(feature_axis=2)
    y_train = y_scaler.fit_transform(y_train_unscaled)
    y_test = y_scaler.transform(y_test_unscaled)
    
    y_train = y_train.reshape(y_train.shape[0], -1) 
    y_test = y_test.reshape(y_test.shape[0], -1)
    X_train, X_test = np.nan_to_num(X_train), np.nan_to_num(X_test) 
    return X_train, y_train, X_test, y_test 


## Univariate without time information

In [28]:
df = pd.read_parquet('/workspace/data.parquet')
df = df[(df.index >= pd.Timestamp('2020-01-01')) & (df.index < pd.Timestamp('2023-01-01'))]
assets = ['BTC']
df = df[[c for c in df.columns if 'quote asset volume' in c and any(asset in c for asset in assets)]]
df.columns = [c.replace(' quote asset volume', '') for c in df.columns]
compare_models(
    generate = lambda sequence_length, n_ahead: generate_data(df = df, sequence_length = sequence_length, n_ahead = n_ahead),
    exp_name="btc_linearnet_results/btc_univariate_without_time",
    n_run=1
)

Sequence Length: 3, Model: Linear_Regression, N_ahead: 1, Run: 1, Time: 0.00s, R2: 0.4115
Sequence Length: 3, Model: Ridge, N_ahead: 1, Run: 1, Time: 0.00s, R2: 0.4102
Sequence Length: 3, Model: LSTM-Encoder-Decoder, N_ahead: 1, Run: 1, Time: 6.64s, RMSE: 0.0550
Sequence Length: 3, Model: LSTM-Shared-Encoder-Decoder, N_ahead: 1, Run: 1, Time: 9.81s, RMSE: 0.0559
Sequence Length: 3, Model: GRU-Last-Sequence, N_ahead: 1, Run: 1, Time: 7.83s, RMSE: 0.0567
Sequence Length: 3, Model: GRU-Full-Sequence, N_ahead: 1, Run: 1, Time: 7.09s, RMSE: 0.0547
Sequence Length: 3, Model: MLP-1-Layer-linear, N_ahead: 1, Run: 1, Time: 5.41s, RMSE: 0.0547
Sequence Length: 3, Model: MLP-2-Layer-linear, N_ahead: 1, Run: 1, Time: 3.26s, RMSE: 0.0545
Sequence Length: 3, Model: MLP-3-Layer-ReLU, N_ahead: 1, Run: 1, Time: 4.70s, RMSE: 0.0549
Sequence Length: 3, Model: LinearNet, N_ahead: 1, Run: 1, Time: 5.93s, RMSE: 0.0544
Sequence Length: 3, Model: LinearNet_no_convolution, N_ahead: 1, Run: 1, Time: 6.05s, RMSE

/usr/local/lib/python3.10/dist-packages/numpy/core/fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:129: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:206: RuntimeWarning: Degrees of freedom <= 0 for slice
  ret = _var(a, axis=axis, dtype=dtype, out=out, ddof=ddof,
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:163: RuntimeWarning: invalid value encountered in divide
  arrmean = um.true_divide(arrmean, div, out=arrmean,
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:198: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)


model                   Linear_Regression     Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                    
1       3                        0.411456  0.410221             0.396844   
        10                       0.410778  0.409368             0.375648   
        20                       0.415087  0.413687             0.335017   
        50                        0.41637   0.41509             0.370108   
        100                      0.415684  0.414425             0.319574   
        200                           NaN       NaN             0.361521   
        400                           NaN       NaN             0.322088   
6       3                        0.134658   0.13459             0.136611   
        10                       0.147954  0.147733             0.093052   
        20                        0.16974   0.16951             0.155732   
        50                       0.172972  0.172895            -0.073816   
        100                       0.17021  0.170236            -0.104864   
        200                           NaN       NaN             0.007329   
        400                           NaN       NaN             0.169929   
15      3                        0.070491  0.070554             0.082664   
        10                       0.093838  0.093792             0.081953   
        20                       0.117428    0.1174             0.008282   
        50                        0.11733  0.117481            -0.141169   
        100                      0.114332  0.114593            -0.138538   
        200                           NaN       NaN             0.024659   
        400                           NaN       NaN             0.124689   
30      3                        0.055361  0.055428             0.063692   
        10                       0.076032  0.076043             0.080383   
        20                       0.090092  0.090142             0.075453   
        50                       0.091726  0.091892             0.087346   
        100                      0.088772  0.089053             0.018917   
        200                           NaN       NaN             0.092228   
        400                           NaN       NaN             0.112116   
90      3                        0.031913  0.031958             0.036459   
        10                       0.046474  0.046502             0.044304   
        20                       0.055769   0.05583             0.049669   
        50                       0.058523  0.058687             0.048333   
        100                      0.064853  0.065127             0.051387   
        200                           NaN       NaN             0.074556   
        400                           NaN       NaN             0.053267   
180     3                        0.033283   0.03331             0.035173   
        10                       0.049776  0.049797             0.049261   
        20                       0.062195  0.062256              0.05732   
        50                       0.072301  0.072483             0.056257   
        100                       0.08373  0.084029             0.057391   
        200                           NaN       NaN             0.052998   
        400                           NaN       NaN             0.056931   
360     3                        0.027958   0.02804             0.023468   
        10                       0.040364  0.040422             0.024856   
        20                       0.049943  0.050016             0.037676   
        50                       0.058338  0.058481             0.033765   
        100                      0.070918  0.071151             0.023306   
        200                           NaN       NaN             0.041899   
        400                           NaN       NaN             0.024184   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                           

R2 Scores Std:


model                   Linear_Regression Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                
1       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
6       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
15      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
30      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
90      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
180     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
360     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                                                 
1       3                                       0.0               0.0   
        10                                      0.0               0.0   
        20                         

...

model                   Linear_Regression     Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                    
1       3                        0.002636  0.002495             6.643296   
        10                       0.007744  0.003137             7.572683   
        20                       0.010783  0.003214             9.039488   
        50                       0.022926  0.010586            13.051321   
        100                      0.052903  0.032367            23.677729   
        200                           NaN       NaN            32.489901   
        400                           NaN       NaN            59.224815   
6       3                        0.004071  0.002555             8.913985   
        10                       0.007165  0.004216            10.007207   
        20                       0.013009  0.005073            11.152779   
        50                        0.02283  0.009482            19.716107   
        100                      0.063876  0.097021            30.366873   
        200                           NaN       NaN            47.079207   
        400                           NaN       NaN            85.508657   
15      3                        0.007921  0.003885            10.824682   
        10                       0.012258  0.004817            12.929383   
        20                       0.020452  0.005539            13.576217   
        50                       0.028547  0.009662            18.840439   
        100                      0.057173  0.147903            25.860358   
        200                           NaN       NaN            39.014194   
        400                           NaN       NaN            60.420967   
30      3                        0.008472  0.005075             9.820038   
        10                       0.010926  0.005255            14.989054   
        20                       0.016771  0.007315            14.768205   
        50                       0.037127  0.108902            19.217918   
        100                      0.071482   0.10325            31.500294   
        200                           NaN       NaN            37.906448   
        400                           NaN       NaN            60.201644   
90      3                        0.021264  0.010067            17.111251   
        10                        0.02395   0.01021            18.434253   
        20                       0.030074  0.078185            19.641855   
        50                       0.051213  0.016613            21.395811   
        100                       0.20995   0.09872            26.076024   
        200                           NaN       NaN            51.688922   
        400                           NaN       NaN            54.699157   
180     3                         0.04638  0.081663            28.596069   
        10                       0.052021  0.173139            27.498944   
        20                       0.062917   0.11018            29.452063   
        50                       0.080391  0.113275            30.232663   
        100                      0.195015  0.040559            34.650085   
        200                           NaN       NaN            53.318535   
        400                           NaN       NaN             57.71538   
360     3                        0.103508  0.035711            52.298375   
        10                       0.187802  0.112752             46.79986   
        20                       0.112679  0.115444            47.402276   
        50                       0.691487  0.163799            48.142473   
        100                      0.776897  0.150653            52.071945   
        200                           NaN       NaN            78.709906   
        400                           NaN       NaN            79.703037   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                           


Training Times Std:


model                   Linear_Regression Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                
1       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
6       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
15      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
30      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
90      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
180     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
360     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                                                 
1       3                                       0.0               0.0   
        10                                      0.0               0.0   
        20                         


Number of Parameters:


model                   Linear_Regression    Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                   
1       3                             4.0      4.0              30651.0   
        10                           11.0     11.0              30651.0   
        20                           21.0     21.0              30651.0   
        50                           51.0     51.0              30651.0   
        100                         101.0    101.0              30651.0   
        200                           NaN      NaN              30651.0   
        400                           NaN      NaN              30651.0   
6       3                            24.0     24.0              30651.0   
        10                           66.0     66.0              30651.0   
        20                          126.0    126.0              30651.0   
        50                          306.0    306.0              30651.0   
        100                         606.0    606.0              30651.0   
        200                           NaN      NaN              30651.0   
        400                           NaN      NaN              30651.0   
15      3                            60.0     60.0              30651.0   
        10                          165.0    165.0              30651.0   
        20                          315.0    315.0              30651.0   
        50                          765.0    765.0              30651.0   
        100                        1515.0   1515.0              30651.0   
        200                           NaN      NaN              30651.0   
        400                           NaN      NaN              30651.0   
30      3                           120.0    120.0              30651.0   
        10                          330.0    330.0              30651.0   
        20                          630.0    630.0              30651.0   
        50                         1530.0   1530.0              30651.0   
        100                        3030.0   3030.0              30651.0   
        200                           NaN      NaN              30651.0   
        400                           NaN      NaN              30651.0   
90      3                           360.0    360.0              30651.0   
        10                          990.0    990.0              30651.0   
        20                         1890.0   1890.0              30651.0   
        50                         4590.0   4590.0              30651.0   
        100                        9090.0   9090.0              30651.0   
        200                           NaN      NaN              30651.0   
        400                           NaN      NaN              30651.0   
180     3                           720.0    720.0              30651.0   
        10                         1980.0   1980.0              30651.0   
        20                         3780.0   3780.0              30651.0   
        50                         9180.0   9180.0              30651.0   
        100                       18180.0  18180.0              30651.0   
        200                           NaN      NaN              30651.0   
        400                           NaN      NaN              30651.0   
360     3                          1440.0   1440.0              30651.0   
        10                         3960.0   3960.0              30651.0   
        20                         7560.0   7560.0              30651.0   
        50                        18360.0  18360.0              30651.0   
        100                       36360.0  36360.0              30651.0   
        200                           NaN      NaN              30651.0   
        400                           NaN      NaN              30651.0   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                                                 
1       3                   

## Univariate + time information (so multivariate but only BTC info)

In [29]:
df = pd.read_parquet('/workspace/data.parquet')
df = df[(df.index >= pd.Timestamp('2020-01-01')) & (df.index < pd.Timestamp('2023-01-01'))]
assets = ['BTC']
df = df[[c for c in df.columns if 'quote asset volume' in c and any(asset in c for asset in assets)]]
df.columns = [c.replace(' quote asset volume', '') for c in df.columns]
df['hour'] = df.reset_index()['group'].apply(lambda x: x.hour).values
df['dayofweek'] = df.reset_index()['group'].apply(lambda x: x.dayofweek).values
compare_models(
    generate = lambda sequence_length, n_ahead: generate_data(df = df, sequence_length = sequence_length, n_ahead = n_ahead),
    exp_name="btc_linearnet_results/btc_univariate_with_time",
    n_run=1
)

Sequence Length: 3, Model: Linear_Regression, N_ahead: 1, Run: 1, Time: 0.00s, R2: 0.4137
Sequence Length: 3, Model: Ridge, N_ahead: 1, Run: 1, Time: 0.00s, R2: 0.4124
Sequence Length: 3, Model: LSTM-Encoder-Decoder, N_ahead: 1, Run: 1, Time: 7.48s, RMSE: 0.0553
Sequence Length: 3, Model: LSTM-Shared-Encoder-Decoder, N_ahead: 1, Run: 1, Time: 9.26s, RMSE: 0.0580
Sequence Length: 3, Model: GRU-Last-Sequence, N_ahead: 1, Run: 1, Time: 7.48s, RMSE: 0.0547
Sequence Length: 3, Model: GRU-Full-Sequence, N_ahead: 1, Run: 1, Time: 8.54s, RMSE: 0.0553
Sequence Length: 3, Model: MLP-1-Layer-linear, N_ahead: 1, Run: 1, Time: 8.56s, RMSE: 0.0545
Sequence Length: 3, Model: MLP-2-Layer-linear, N_ahead: 1, Run: 1, Time: 4.74s, RMSE: 0.0543
Sequence Length: 3, Model: MLP-3-Layer-ReLU, N_ahead: 1, Run: 1, Time: 4.88s, RMSE: 0.0548
Sequence Length: 3, Model: LinearNet, N_ahead: 1, Run: 1, Time: 7.36s, RMSE: 0.0540
Sequence Length: 3, Model: LinearNet_no_convolution, N_ahead: 1, Run: 1, Time: 6.98s, RMSE

/usr/local/lib/python3.10/dist-packages/numpy/core/fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:129: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:206: RuntimeWarning: Degrees of freedom <= 0 for slice
  ret = _var(a, axis=axis, dtype=dtype, out=out, ddof=ddof,
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:163: RuntimeWarning: invalid value encountered in divide
  arrmean = um.true_divide(arrmean, div, out=arrmean,
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:198: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)


model                   Linear_Regression     Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                    
1       3                        0.413675  0.412421             0.390678   
        10                       0.416256  0.414726             0.416665   
        20                       0.428007  0.426562             0.373278   
        50                       0.428373  0.427041              0.36423   
        100                      0.426377  0.425067             0.408267   
        200                           NaN       NaN             0.391524   
        400                           NaN       NaN             0.386741   
6       3                        0.146177  0.146108             0.152419   
        10                       0.179504  0.179219              0.17634   
        20                       0.204436  0.204214             0.176318   
        50                       0.204927  0.204792             0.175313   
        100                      0.200474  0.200469             0.148986   
        200                           NaN       NaN             0.136885   
        400                           NaN       NaN             0.175795   
15      3                        0.090545  0.090608             0.115437   
        10                       0.132147  0.132093             0.103891   
        20                       0.151132   0.15114             0.118281   
        50                       0.150746  0.150857             0.056428   
        100                      0.152401  0.152599             -0.19033   
        200                           NaN       NaN             0.014194   
        400                           NaN       NaN             0.095634   
30      3                        0.071502   0.07157             0.110035   
        10                       0.106051  0.106045             0.131368   
        20                       0.124558   0.12461             0.123105   
        50                       0.126222  0.126356             0.096897   
        100                      0.136785  0.137019             0.094862   
        200                           NaN       NaN             0.094484   
        400                           NaN       NaN             0.092845   
90      3                        0.049125  0.049173             0.080114   
        10                       0.079662  0.079678             0.112038   
        20                       0.096465  0.096512             0.124066   
        50                        0.10665  0.106784             0.105224   
        100                      0.123126  0.123389             0.112476   
        200                           NaN       NaN             0.112643   
        400                           NaN       NaN             0.103994   
180     3                        0.056711  0.056737             0.045117   
        10                       0.092701  0.092706             0.060877   
        20                       0.114414  0.114467             0.063714   
        50                       0.125996   0.12617             0.064696   
        100                      0.137457  0.137785             0.059375   
        200                           NaN       NaN             0.067357   
        400                           NaN       NaN             0.064259   
360     3                        0.055361  0.055439             0.021637   
        10                       0.087723  0.087779             0.033619   
        20                       0.107165  0.107257             0.039274   
        50                        0.11801  0.118184             0.028027   
        100                      0.131801  0.132117             0.039656   
        200                           NaN       NaN              0.02317   
        400                           NaN       NaN             0.027863   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                           

R2 Scores Std:


model                   Linear_Regression Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                
1       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
6       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
15      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
30      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
90      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
180     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
360     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                                                 
1       3                                       0.0               0.0   
        10                                      0.0               0.0   
        20                         

...

model                   Linear_Regression     Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                    
1       3                         0.00483  0.002524             7.483512   
        10                       0.014536  0.004695             7.507601   
        20                       0.031094  0.010937            11.117093   
        50                       0.131239  0.110898             15.41793   
        100                      0.596962  0.205596            24.050967   
        200                           NaN       NaN            41.001209   
        400                           NaN       NaN            65.359262   
6       3                        0.007923  0.003932            11.062274   
        10                       0.019657  0.007855             10.55185   
        20                       0.029272  0.012098            11.306881   
        50                       0.218612  0.111827            12.664526   
        100                      0.788776  0.213975            21.878634   
        200                           NaN       NaN            31.160106   
        400                           NaN       NaN            42.810917   
15      3                        0.011213  0.004737             11.12883   
        10                       0.028131  0.009761            12.305589   
        20                       0.048932  0.018156             16.81369   
        50                       0.162745  0.111829            16.428016   
        100                      0.687853  0.220888            26.348004   
        200                           NaN       NaN            34.651114   
        400                           NaN       NaN            53.174698   
30      3                        0.012015  0.006156            15.989243   
        10                        0.02287  0.008933             18.29961   
        20                       0.038549  0.024149            17.334651   
        50                       0.242305  0.116303            20.379467   
        100                      1.429698  0.528681              28.6374   
        200                           NaN       NaN            54.899219   
        400                           NaN       NaN            60.114818   
90      3                        0.024174  0.009344            33.823621   
        10                       0.040569  0.162726             32.01915   
        20                       0.138224  0.094359             41.80067   
        50                       0.244493  0.119845            36.328119   
        100                      1.011159  0.192036            41.107244   
        200                           NaN       NaN            61.563328   
        400                           NaN       NaN           132.607058   
180     3                        0.052197   0.14519            29.733554   
        10                       0.076525  0.114492            35.834702   
        20                       0.092577    0.1879            33.822124   
        50                       0.455226  0.117765            44.513464   
        100                       1.19609   0.20038              33.6034   
        200                           NaN       NaN            57.600528   
        400                           NaN       NaN            75.856913   
360     3                        0.108318  0.038405            45.178966   
        10                       0.266533  0.213902            57.091249   
        20                       0.320509  0.188962            69.679726   
        50                       0.615268  0.186672            49.443768   
        100                      1.395552  0.294966            69.955339   
        200                           NaN       NaN             59.71597   
        400                           NaN       NaN            89.325612   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                           


Training Times Std:


model                   Linear_Regression Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                
1       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
6       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
15      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
30      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
90      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
180     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
360     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                                                 
1       3                                       0.0               0.0   
        10                                      0.0               0.0   
        20                         


Number of Parameters:


model                   Linear_Regression     Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                    
1       3                            10.0      10.0              31051.0   
        10                           31.0      31.0              31051.0   
        20                           61.0      61.0              31051.0   
        50                          151.0     151.0              31051.0   
        100                         301.0     301.0              31051.0   
        200                           NaN       NaN              31051.0   
        400                           NaN       NaN              31051.0   
6       3                            60.0      60.0              31051.0   
        10                          186.0     186.0              31051.0   
        20                          366.0     366.0              31051.0   
        50                          906.0     906.0              31051.0   
        100                        1806.0    1806.0              31051.0   
        200                           NaN       NaN              31051.0   
        400                           NaN       NaN              31051.0   
15      3                           150.0     150.0              31051.0   
        10                          465.0     465.0              31051.0   
        20                          915.0     915.0              31051.0   
        50                         2265.0    2265.0              31051.0   
        100                        4515.0    4515.0              31051.0   
        200                           NaN       NaN              31051.0   
        400                           NaN       NaN              31051.0   
30      3                           300.0     300.0              31051.0   
        10                          930.0     930.0              31051.0   
        20                         1830.0    1830.0              31051.0   
        50                         4530.0    4530.0              31051.0   
        100                        9030.0    9030.0              31051.0   
        200                           NaN       NaN              31051.0   
        400                           NaN       NaN              31051.0   
90      3                           900.0     900.0              31051.0   
        10                         2790.0    2790.0              31051.0   
        20                         5490.0    5490.0              31051.0   
        50                        13590.0   13590.0              31051.0   
        100                       27090.0   27090.0              31051.0   
        200                           NaN       NaN              31051.0   
        400                           NaN       NaN              31051.0   
180     3                          1800.0    1800.0              31051.0   
        10                         5580.0    5580.0              31051.0   
        20                        10980.0   10980.0              31051.0   
        50                        27180.0   27180.0              31051.0   
        100                       54180.0   54180.0              31051.0   
        200                           NaN       NaN              31051.0   
        400                           NaN       NaN              31051.0   
360     3                          3600.0    3600.0              31051.0   
        10                        11160.0   11160.0              31051.0   
        20                        21960.0   21960.0              31051.0   
        50                        54360.0   54360.0              31051.0   
        100                      108360.0  108360.0              31051.0   
        200                           NaN       NaN              31051.0   
        400                           NaN       NaN              31051.0   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                           

## Multivariate without time information

In [30]:
df = pd.read_parquet('/workspace/data.parquet')
df = df[(df.index >= pd.Timestamp('2020-01-01')) & (df.index < pd.Timestamp('2023-01-01'))]
assets = ['BTC', 'ETH', 'ADA', 'XMR', 'EOS', 'MATIC', 'TRX', 'FTM', 'BNB', 'XLM', 'ENJ', 'CHZ', 'BUSD', 'ATOM', 'LINK', 'ETC', 'XRP', 'BCH', 'LTC']
df = df[[c for c in df.columns if 'quote asset volume' in c and any(asset in c for asset in assets)]]
df.columns = [c.replace(' quote asset volume', '') for c in df.columns]
compare_models(
    generate = lambda sequence_length, n_ahead: generate_data(df = df, sequence_length = sequence_length, n_ahead = n_ahead),
    exp_name="btc_linearnet_results/btc_multivariate_without_time",
    n_run=1
)

Sequence Length: 3, Model: Linear_Regression, N_ahead: 1, Run: 1, Time: 0.03s, R2: 0.4080
Sequence Length: 3, Model: Ridge, N_ahead: 1, Run: 1, Time: 0.01s, R2: 0.4051
Sequence Length: 3, Model: LSTM-Encoder-Decoder, N_ahead: 1, Run: 1, Time: 6.93s, RMSE: 0.0543
Sequence Length: 3, Model: LSTM-Shared-Encoder-Decoder, N_ahead: 1, Run: 1, Time: 7.16s, RMSE: 0.0549
Sequence Length: 3, Model: GRU-Last-Sequence, N_ahead: 1, Run: 1, Time: 7.40s, RMSE: 0.0554
Sequence Length: 3, Model: GRU-Full-Sequence, N_ahead: 1, Run: 1, Time: 7.61s, RMSE: 0.0545
Sequence Length: 3, Model: MLP-1-Layer-linear, N_ahead: 1, Run: 1, Time: 3.87s, RMSE: 0.0554
Sequence Length: 3, Model: MLP-2-Layer-linear, N_ahead: 1, Run: 1, Time: 3.85s, RMSE: 0.0546
Sequence Length: 3, Model: MLP-3-Layer-ReLU, N_ahead: 1, Run: 1, Time: 4.58s, RMSE: 0.0572
Sequence Length: 3, Model: LinearNet, N_ahead: 1, Run: 1, Time: 8.13s, RMSE: 0.0544
Sequence Length: 3, Model: LinearNet_no_convolution, N_ahead: 1, Run: 1, Time: 6.69s, RMSE

/usr/local/lib/python3.10/dist-packages/numpy/core/fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:129: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:206: RuntimeWarning: Degrees of freedom <= 0 for slice
  ret = _var(a, axis=axis, dtype=dtype, out=out, ddof=ddof,
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:163: RuntimeWarning: invalid value encountered in divide
  arrmean = um.true_divide(arrmean, div, out=arrmean,
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:198: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)


model                   Linear_Regression     Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                    
1       3                         0.40805  0.405084               0.4114   
        10                       0.401578  0.399028             0.392533   
        20                       0.398003  0.396897             0.399778   
        50                       0.380912  0.385737             0.394891   
        100                        0.3561  0.370567             0.395413   
        200                           NaN       NaN             0.394376   
        400                           NaN       NaN             0.394531   
6       3                        0.136252  0.136682             0.127164   
        10                        0.14052   0.14162             -0.01963   
        20                       0.154986  0.157475             0.115756   
        50                       0.137769  0.146645             0.077422   
        100                      0.108888  0.126513             0.132649   
        200                           NaN       NaN             0.122369   
        400                           NaN       NaN             0.085662   
15      3                        0.067197  0.067987             -0.12456   
        10                       0.085357  0.086759            -0.095532   
        20                       0.101344  0.104591             0.047099   
        50                       0.086676  0.096216            -0.212483   
        100                      0.051523   0.06978            -0.070567   
        200                           NaN       NaN            -0.000587   
        400                           NaN       NaN            -0.107605   
30      3                         0.05285  0.053614             0.049864   
        10                       0.067545  0.069327             0.038354   
        20                       0.074763  0.078597             0.006843   
        50                       0.063631  0.072979            -0.073555   
        100                      0.029132  0.047067              0.01688   
        200                           NaN       NaN             0.041372   
        400                           NaN       NaN            -0.048284   
90      3                        0.025832  0.026456             0.026092   
        10                       0.037762  0.039251             0.019285   
        20                       0.044289  0.047365             0.026867   
        50                       0.031656  0.040204              0.01736   
        100                     -0.006333  0.013121             0.024014   
        200                           NaN       NaN               0.0159   
        400                           NaN       NaN             0.025914   
180     3                        0.021881  0.022901             0.022153   
        10                       0.033592  0.035739             0.018058   
        20                       0.039521  0.043562              0.02687   
        50                        0.02502  0.035407             0.029974   
        100                     -0.020853  0.002318            -0.001201   
        200                           NaN       NaN             -0.00814   
        400                           NaN       NaN             0.018835   
360     3                       -0.001107  0.002457            -0.009575   
        10                      -0.003426  0.001211            -0.026817   
        20                      -0.008391 -0.001267            -0.109802   
        50                      -0.044459 -0.027966            -0.167106   
        100                     -0.117231 -0.081521            -0.139027   
        200                           NaN       NaN            -0.237851   
        400                           NaN       NaN            -0.179322   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                           

R2 Scores Std:


model                   Linear_Regression Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                
1       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
6       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
15      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
30      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
90      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
180     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
360     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                                                 
1       3                                       0.0               0.0   
        10                                      0.0               0.0   
        20                         

...

model                   Linear_Regression     Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                    
1       3                        0.027572  0.010152             6.934581   
        10                       0.205285  0.188525             7.030656   
        20                       0.947808  0.249677            10.008736   
        50                       4.341307   0.60844            14.768981   
        100                     11.004221   0.98079            18.017756   
        200                           NaN       NaN            37.270296   
        400                           NaN       NaN            51.837157   
6       3                        0.029871  0.011683              7.63825   
        10                       0.191244  0.197374             9.747306   
        20                       0.761944  0.191452            11.237277   
        50                       4.623498  0.600151            12.138794   
        100                     11.734021   0.98931            16.822811   
        200                           NaN       NaN            26.950118   
        400                           NaN       NaN            44.492527   
15      3                        0.031602  0.014207            10.519508   
        10                       0.259463     0.183              9.85284   
        20                        1.07804  0.189039            10.625398   
        50                       3.984298  0.542573            13.207247   
        100                     12.213547  0.942079            17.682662   
        200                           NaN       NaN            26.745153   
        400                           NaN       NaN            57.125002   
30      3                        0.041203  0.166671             9.927149   
        10                       0.330474   0.10517            10.763213   
        20                        1.13676  0.185437            16.337454   
        50                       4.528459  0.600406            17.991597   
        100                     12.702824  0.971919            21.781354   
        200                           NaN       NaN            35.151958   
        400                           NaN       NaN            59.998559   
90      3                        0.189582  0.021333            16.055494   
        10                       0.432198  0.135044            19.537148   
        20                       1.223983  0.126049             19.30635   
        50                       5.228368  0.701365            20.463018   
        100                     13.921176  1.024792            26.197448   
        200                           NaN       NaN            35.823504   
        400                           NaN       NaN            54.956279   
180     3                         0.24823   0.18532            28.742018   
        10                       0.673445   0.26964            26.442784   
        20                       1.627206   0.22502             26.50543   
        50                        5.50209  0.795979            29.302974   
        100                     14.193552  1.304559            33.805272   
        200                           NaN       NaN            42.908764   
        400                           NaN       NaN            61.035176   
360     3                        0.360721    0.2715            42.792548   
        10                        0.85029  0.187196            43.693634   
        20                       1.840698  0.284736            44.368512   
        50                       6.791722   0.89292             54.33456   
        100                     15.954366  1.398757            51.498252   
        200                           NaN       NaN            66.439559   
        400                           NaN       NaN            78.031775   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                           


Training Times Std:


model                   Linear_Regression Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                
1       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
6       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
15      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
30      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
90      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
180     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
360     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                                                 
1       3                                       0.0               0.0   
        10                                      0.0               0.0   
        20                         


Number of Parameters:


model                   Linear_Regression     Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                    
1       3                            58.0      58.0              34251.0   
        10                          191.0     191.0              34251.0   
        20                          381.0     381.0              34251.0   
        50                          951.0     951.0              34251.0   
        100                        1901.0    1901.0              34251.0   
        200                           NaN       NaN              34251.0   
        400                           NaN       NaN              34251.0   
6       3                           348.0     348.0              34251.0   
        10                         1146.0    1146.0              34251.0   
        20                         2286.0    2286.0              34251.0   
        50                         5706.0    5706.0              34251.0   
        100                       11406.0   11406.0              34251.0   
        200                           NaN       NaN              34251.0   
        400                           NaN       NaN              34251.0   
15      3                           870.0     870.0              34251.0   
        10                         2865.0    2865.0              34251.0   
        20                         5715.0    5715.0              34251.0   
        50                        14265.0   14265.0              34251.0   
        100                       28515.0   28515.0              34251.0   
        200                           NaN       NaN              34251.0   
        400                           NaN       NaN              34251.0   
30      3                          1740.0    1740.0              34251.0   
        10                         5730.0    5730.0              34251.0   
        20                        11430.0   11430.0              34251.0   
        50                        28530.0   28530.0              34251.0   
        100                       57030.0   57030.0              34251.0   
        200                           NaN       NaN              34251.0   
        400                           NaN       NaN              34251.0   
90      3                          5220.0    5220.0              34251.0   
        10                        17190.0   17190.0              34251.0   
        20                        34290.0   34290.0              34251.0   
        50                        85590.0   85590.0              34251.0   
        100                      171090.0  171090.0              34251.0   
        200                           NaN       NaN              34251.0   
        400                           NaN       NaN              34251.0   
180     3                         10440.0   10440.0              34251.0   
        10                        34380.0   34380.0              34251.0   
        20                        68580.0   68580.0              34251.0   
        50                       171180.0  171180.0              34251.0   
        100                      342180.0  342180.0              34251.0   
        200                           NaN       NaN              34251.0   
        400                           NaN       NaN              34251.0   
360     3                         20880.0   20880.0              34251.0   
        10                        68760.0   68760.0              34251.0   
        20                       137160.0  137160.0              34251.0   
        50                       342360.0  342360.0              34251.0   
        100                      684360.0  684360.0              34251.0   
        200                           NaN       NaN              34251.0   
        400                           NaN       NaN              34251.0   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                           

## Multivariate with time information

In [31]:
df = pd.read_parquet('/workspace/data.parquet')
df = df[(df.index >= pd.Timestamp('2020-01-01')) & (df.index < pd.Timestamp('2023-01-01'))]
assets = ['BTC', 'ETH', 'ADA', 'XMR', 'EOS', 'MATIC', 'TRX', 'FTM', 'BNB', 'XLM', 'ENJ', 'CHZ', 'BUSD', 'ATOM', 'LINK', 'ETC', 'XRP', 'BCH', 'LTC']
df = df[[c for c in df.columns if 'quote asset volume' in c and any(asset in c for asset in assets)]]
df.columns = [c.replace(' quote asset volume', '') for c in df.columns]
df['hour'] = df.reset_index()['group'].apply(lambda x: x.hour).values
df['dayofweek'] = df.reset_index()['group'].apply(lambda x: x.dayofweek).values
compare_models(
    generate = lambda sequence_length, n_ahead: generate_data(df = df, sequence_length = sequence_length, n_ahead = n_ahead),
    exp_name="btc_linearnet_results/btc_multivariate_with_time",
    n_run=1
)

Sequence Length: 3, Model: Linear_Regression, N_ahead: 1, Run: 1, Time: 0.03s, R2: 0.4083
Sequence Length: 3, Model: Ridge, N_ahead: 1, Run: 1, Time: 0.01s, R2: 0.4052
Sequence Length: 3, Model: LSTM-Encoder-Decoder, N_ahead: 1, Run: 1, Time: 7.26s, RMSE: 0.0544
Sequence Length: 3, Model: LSTM-Shared-Encoder-Decoder, N_ahead: 1, Run: 1, Time: 7.87s, RMSE: 0.0549
Sequence Length: 3, Model: GRU-Last-Sequence, N_ahead: 1, Run: 1, Time: 8.19s, RMSE: 0.0561
Sequence Length: 3, Model: GRU-Full-Sequence, N_ahead: 1, Run: 1, Time: 7.96s, RMSE: 0.0561
Sequence Length: 3, Model: MLP-1-Layer-linear, N_ahead: 1, Run: 1, Time: 4.81s, RMSE: 0.0553
Sequence Length: 3, Model: MLP-2-Layer-linear, N_ahead: 1, Run: 1, Time: 4.19s, RMSE: 0.0547
Sequence Length: 3, Model: MLP-3-Layer-ReLU, N_ahead: 1, Run: 1, Time: 5.43s, RMSE: 0.0560
Sequence Length: 3, Model: LinearNet, N_ahead: 1, Run: 1, Time: 8.59s, RMSE: 0.0552
Sequence Length: 3, Model: LinearNet_no_convolution, N_ahead: 1, Run: 1, Time: 7.47s, RMSE

/usr/local/lib/python3.10/dist-packages/numpy/core/fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:129: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:206: RuntimeWarning: Degrees of freedom <= 0 for slice
  ret = _var(a, axis=axis, dtype=dtype, out=out, ddof=ddof,
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:163: RuntimeWarning: invalid value encountered in divide
  arrmean = um.true_divide(arrmean, div, out=arrmean,
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:198: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)


model                   Linear_Regression     Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                    
1       3                        0.408315  0.405232             0.409537   
        10                       0.404174  0.401326             0.394461   
        20                        0.41129  0.409579             0.402508   
        50                       0.393305  0.397576             0.398681   
        100                      0.363804  0.377445             0.399127   
        200                           NaN       NaN             0.383718   
        400                           NaN       NaN             0.403973   
6       3                        0.144478  0.144952             0.111021   
        10                       0.166146   0.16728             0.092293   
        20                       0.188575  0.190556             0.162229   
        50                       0.166752  0.174765             0.084982   
        100                      0.128543  0.145713             0.114354   
        200                           NaN       NaN             0.154061   
        400                           NaN       NaN             0.066713   
15      3                        0.085498  0.086342             0.011511   
        10                       0.121332  0.122793            -0.057617   
        20                       0.134709  0.137635            -0.023898   
        50                       0.113702  0.122645             0.031949   
        100                      0.079078  0.096689            -0.351351   
        200                           NaN       NaN             0.060018   
        400                           NaN       NaN            -0.145144   
30      3                          0.0676  0.068388             -0.00735   
        10                       0.094472  0.096265             0.018388   
        20                       0.106598  0.110001             0.001378   
        50                       0.089078  0.098127             0.083341   
        100                      0.068191  0.086187             0.066883   
        200                           NaN       NaN             0.099906   
        400                           NaN       NaN             0.066468   
90      3                        0.042356  0.042988             0.036163   
        10                       0.068023   0.06951             0.047582   
        20                       0.079841  0.082784             0.053802   
        50                       0.074261  0.082362             0.041385   
        100                      0.053456  0.072848             0.050862   
        200                           NaN       NaN             0.020395   
        400                           NaN       NaN              0.04223   
180     3                        0.045201  0.046173             0.028885   
        10                       0.074672  0.076711             0.030879   
        20                       0.089701  0.093437             0.036576   
        50                       0.078764  0.088502             0.032397   
        100                      0.037426  0.060379             0.020579   
        200                           NaN       NaN             0.011542   
        400                           NaN       NaN             0.037181   
360     3                         0.02612  0.029585             0.003603   
        10                       0.042206  0.046675            -0.013937   
        20                       0.046716  0.053487            -0.039694   
        50                       0.017105  0.032636            -0.066875   
        100                     -0.056751 -0.013676            -0.078928   
        200                           NaN       NaN            -0.179821   
        400                           NaN       NaN            -0.050817   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                           

R2 Scores Std:


model                   Linear_Regression Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                
1       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
6       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
15      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
30      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
90      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
180     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
360     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                                                 
1       3                                       0.0               0.0   
        10                                      0.0               0.0   
        20                         

...

model                   Linear_Regression     Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                    
1       3                        0.030297  0.012842             7.261701   
        10                       0.281172  0.203999              9.63306   
        20                       1.135018  0.247337             9.971595   
        50                        4.49724  0.383496            13.005648   
        100                     14.874139  1.073438            21.403485   
        200                           NaN       NaN            31.317586   
        400                           NaN       NaN              59.0998   
6       3                        0.033906  0.013678             8.372897   
        10                       0.322894  0.191151            10.476137   
        20                       1.572875  0.246053            10.145939   
        50                       4.652858  0.318954            14.683906   
        100                     14.561799  1.177057            18.674293   
        200                           NaN       NaN            33.430799   
        400                           NaN       NaN            59.108518   
15      3                        0.033559  0.016591             11.84479   
        10                       0.341414  0.204757             12.36658   
        20                        1.55185  0.215488            13.675799   
        50                       5.208598  0.557476            14.501007   
        100                     13.761566  1.123403            20.796631   
        200                           NaN       NaN            28.515447   
        400                           NaN       NaN             57.81514   
30      3                        0.042607  0.104588            15.639946   
        10                       0.405789  0.117069            13.564372   
        20                       1.481394   0.27099            13.493407   
        50                       6.107029  0.448287            18.347662   
        100                     15.672067  1.158252            21.622909   
        200                           NaN       NaN            38.372231   
        400                           NaN       NaN            69.084696   
90      3                        0.064234  0.118335             16.24037   
        10                       0.541041  0.137097            17.126328   
        20                       1.587785  0.219222            18.131135   
        50                       5.381366  0.592109            22.598271   
        100                     17.335507  1.304943            25.728977   
        200                           NaN       NaN            35.619958   
        400                           NaN       NaN            54.925342   
180     3                        0.194547   0.19138            27.238189   
        10                       0.690937    0.1962            25.517956   
        20                        1.85813  0.225714            28.167092   
        50                         6.2523   0.59907            31.535996   
        100                     18.211414  1.300938            34.421259   
        200                           NaN       NaN            54.340699   
        400                           NaN       NaN            62.867358   
360     3                        0.247279  0.191904            43.219296   
        10                       0.902729  0.281049            48.275909   
        20                       2.527737  0.286919            44.963843   
        50                       6.479815   0.60906            54.566821   
        100                     19.945746  1.608693            55.288787   
        200                           NaN       NaN             61.52353   
        400                           NaN       NaN            79.231563   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                           


Training Times Std:


model                   Linear_Regression Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                
1       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
6       3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
15      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
30      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
90      3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
180     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   
360     3                             0.0   0.0                  0.0   
        10                            0.0   0.0                  0.0   
        20                            0.0   0.0                  0.0   
        50                            0.0   0.0                  0.0   
        100                           0.0   0.0                  0.0   
        200                           NaN   NaN                  0.0   
        400                           NaN   NaN                  0.0   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                                                 
1       3                                       0.0               0.0   
        10                                      0.0               0.0   
        20                         


Number of Parameters:


model                   Linear_Regression     Ridge LSTM-Encoder-Decoder  \
n_ahead sequence_length                                                    
1       3                            64.0      64.0              34651.0   
        10                          211.0     211.0              34651.0   
        20                          421.0     421.0              34651.0   
        50                         1051.0    1051.0              34651.0   
        100                        2101.0    2101.0              34651.0   
        200                           NaN       NaN              34651.0   
        400                           NaN       NaN              34651.0   
6       3                           384.0     384.0              34651.0   
        10                         1266.0    1266.0              34651.0   
        20                         2526.0    2526.0              34651.0   
        50                         6306.0    6306.0              34651.0   
        100                       12606.0   12606.0              34651.0   
        200                           NaN       NaN              34651.0   
        400                           NaN       NaN              34651.0   
15      3                           960.0     960.0              34651.0   
        10                         3165.0    3165.0              34651.0   
        20                         6315.0    6315.0              34651.0   
        50                        15765.0   15765.0              34651.0   
        100                       31515.0   31515.0              34651.0   
        200                           NaN       NaN              34651.0   
        400                           NaN       NaN              34651.0   
30      3                          1920.0    1920.0              34651.0   
        10                         6330.0    6330.0              34651.0   
        20                        12630.0   12630.0              34651.0   
        50                        31530.0   31530.0              34651.0   
        100                       63030.0   63030.0              34651.0   
        200                           NaN       NaN              34651.0   
        400                           NaN       NaN              34651.0   
90      3                          5760.0    5760.0              34651.0   
        10                        18990.0   18990.0              34651.0   
        20                        37890.0   37890.0              34651.0   
        50                        94590.0   94590.0              34651.0   
        100                      189090.0  189090.0              34651.0   
        200                           NaN       NaN              34651.0   
        400                           NaN       NaN              34651.0   
180     3                         11520.0   11520.0              34651.0   
        10                        37980.0   37980.0              34651.0   
        20                        75780.0   75780.0              34651.0   
        50                       189180.0  189180.0              34651.0   
        100                      378180.0  378180.0              34651.0   
        200                           NaN       NaN              34651.0   
        400                           NaN       NaN              34651.0   
360     3                         23040.0   23040.0              34651.0   
        10                        75960.0   75960.0              34651.0   
        20                       151560.0  151560.0              34651.0   
        50                       378360.0  378360.0              34651.0   
        100                      756360.0  756360.0              34651.0   
        200                           NaN       NaN              34651.0   
        400                           NaN       NaN              34651.0   

model                   LSTM-Shared-Encoder-Decoder GRU-Last-Sequence  \
n_ahead sequence_length                           

# We have realized after run that the hidden size of the conv1D set in LinearNet wasn't the right one, bellow is fixed + rerun with modification of the tables with only reruning the LinearNet

In [32]:
class SequentialDense(Layer):
    """
    A custom layer that performs sequential dense operations.

    This layer applies dense transformations along both the feature and time dimensions
    of the input sequence.

    Args:
        end_features (int): The number of output features.
        end_sequence_length (int): The length of the output sequence.
        activation (str or callable, optional): Activation function to use. Defaults to 'linear'.
        it_kernel_initializer (keras.initializers.Initializer, optional): Initializer for the input-time kernel. Defaults to RandomUniform(0,1).
        f_kernel_initializer (keras.initializers.Initializer, optional): Initializer for the feature kernel. Defaults to RandomUniform(0,1).
        ot_kernel_initializer (keras.initializers.Initializer, optional): Initializer for the output-time kernel. Defaults to RandomUniform(0,1).
        kernel_regularizer (keras.regularizers.Regularizer, optional): Regularizer function applied to the kernels. Defaults to None.
        **kwargs: Additional keyword arguments passed to the parent Layer class.
    """
    def __init__(self, end_features, end_sequence_length, activation='linear',
                 it_kernel_initializer=keras.initializers.RandomUniform(minval=0.0, maxval=1.0),
                 f_kernel_initializer=keras.initializers.RandomUniform(minval=0.0, maxval=1.0),
                 ot_kernel_initializer=keras.initializers.RandomUniform(minval=0.0, maxval=1.0),
                 kernel_regularizer=None, **kwargs):
        super().__init__(**kwargs)
        self.end_features = end_features
        self.activation = keras.activations.get(activation)
        self.end_sequence_length = end_sequence_length
        self.dense_features = Dense(end_features)
        self.dense_times = Dense(end_sequence_length)
        self.it_kernel_initializer = keras.initializers.get(it_kernel_initializer)
        self.f_kernel_initializer = keras.initializers.get(f_kernel_initializer)
        self.ot_kernel_initializer = keras.initializers.get(ot_kernel_initializer)
        self.kernel_regularizer = keras.regularizers.get(kernel_regularizer)

    def build(self, input_shape):
        _, seq_len, n_features = input_shape
        self.it_kernel = self.add_weight(
            shape=(1, seq_len, 1),
            name="it_kernel",
            initializer=self.it_kernel_initializer,
            regularizer=self.kernel_regularizer,
        )
        self.f_kernel = self.add_weight(
            shape=(1, 1, self.end_features),
            name="f_kernel",
            initializer=self.f_kernel_initializer,
            regularizer=self.kernel_regularizer,
        )
        self.ot_kernel = self.add_weight(
            shape=(1, self.end_sequence_length, 1),
            name="ot_kernel",
            initializer=self.ot_kernel_initializer,
            regularizer=self.kernel_regularizer,
        )
        self.dense_features.build(input_shape)
        self.dense_times.build((input_shape[0], self.end_features, seq_len))
        super().build(input_shape)

    def call(self, inputs):
        x = inputs * self.it_kernel
        x = self.dense_features(x)
        x = x * self.f_kernel
        x = keras.ops.transpose(x, (0, 2, 1))
        x = self.dense_times(x)
        x = keras.ops.transpose(x, (0, 2, 1))
        x = self.ot_kernel * x
        return self.activation(x)

    def compute_output_shape(self, input_shape):
        return (input_shape[0], self.end_sequence_length, self.end_features)

class LinearLayer(Layer):
    """
    A custom layer that applies a linear transformation using pre-computed weights and biases.

    Args:
        equivalent_weights (np.ndarray): Pre-computed weights for the linear transformation.
        equivalent_bias (np.ndarray): Pre-computed bias for the linear transformation.
        **kwargs: Additional keyword arguments passed to the parent Layer class.
    """
    def __init__(self, equivalent_weights, equivalent_bias, **kwargs):
        super().__init__(**kwargs)
        self.equivalent_weights = self.add_weight(
            shape=equivalent_weights.shape,
            initializer=keras.initializers.Constant(equivalent_weights),
            trainable=False,
            name='equivalent_weights'
        )
        self.equivalent_bias = self.add_weight(
            shape=equivalent_bias.shape,
            initializer=keras.initializers.Constant(equivalent_bias),
            trainable=False,
            name='equivalent_bias'
        )

    def call(self, inputs):
        return keras.ops.einsum('bij,ijkl->bkl', inputs, self.equivalent_weights) + self.equivalent_bias

    def get_config(self):
        config = super().get_config()
        config.update({
            "equivalent_weights": keras.ops.convert_to_numpy(self.equivalent_weights),
            "equivalent_bias": keras.ops.convert_to_numpy(self.equivalent_bias)
        })
        return config

class LinearNet(keras.Model):
    """
    A custom model that applies a series of linear transformations to the input.

    Args:
        output_len (int): The length of the output sequence.
        output_features (int, optional): The number of output features. Defaults to 1.
        flatten_output (bool, optional): Whether to flatten the output. Defaults to False.
        hidden_layers (int, optional): The number of hidden layers. Defaults to 1.
        use_convolution (bool, optional): Whether to use convolution layers. Defaults to True.
        hidden_sizes (List[int], optional): List of hidden layer sizes. If not provided, sizes will be calculated at build time.
        kernel_size (Union[int, List[int]], optional): Kernel size(s) for convolution layers. Defaults to 5.
        **kwargs: Additional keyword arguments passed to the parent Model class.
    """
    def __init__(self,
                 output_len: int,
                 output_features: int = 1,
                 flatten_output: bool = False,
                 hidden_layers: int = 1,
                 use_convolution: bool = True,
                 hidden_sizes: Optional[List[int]] = None,
                 kernel_size: Optional[Union[int, List[int]]] = 5,
                 **kwargs):
        super().__init__(**kwargs)
        self.output_len = output_len
        self.output_features = output_features
        self.flatten_output = flatten_output
        self.hidden_layers = hidden_layers
        self.use_convolution = use_convolution
        self.hidden_sizes = hidden_sizes
        self.kernel_size = kernel_size

        # Process kernel_size
        if isinstance(kernel_size, (list, tuple)):
            if len(kernel_size) != hidden_layers:
                raise ValueError(f"Received {len(kernel_size)} values in kernel_size while having {hidden_layers} hidden layers. Please provide the same number of values or only provide one integer if you want to use the same everywhere.")
            self.kernel_size = kernel_size
        else:
            self.kernel_size = [kernel_size] * hidden_layers

        # Layers will be defined in the build method
        self.layers_list = []

    def build(self, input_shape):
        _, self.input_seq_len, self.input_features = input_shape

        # Calculate hidden sizes if not provided
        if self.hidden_sizes is None:
            self.hidden_sizes = [
                int(self.input_features - (i + 1) * (self.output_features - self.input_features) / self.hidden_layers)
                for i in range(self.hidden_layers)
            ]
        elif len(self.hidden_sizes) != self.hidden_layers:
            raise ValueError(f"Received {len(self.hidden_sizes)} values in hidden_sizes while having {self.hidden_layers} hidden layers. Please provide the same number of values.")

        # Define layers
        for i in range(self.hidden_layers):
            if i == self.hidden_layers - 1:
                hidden_size = self.output_features
            else:
                hidden_size = self.hidden_sizes[i]
            
            if self.use_convolution:
                self.layers_list.append(SequentialDense(
                    end_features=hidden_size,
                    end_sequence_length=int(self.output_len + self.kernel_size[i] - 1)
                ))
                self.layers_list.append(Conv1D(
                    filters=hidden_size,
                    kernel_size=self.kernel_size[i],
                    padding='valid'
                ))
            else:
                self.layers_list.append(SequentialDense(
                    end_features=hidden_size,
                    end_sequence_length=self.output_len
                ))

        if self.flatten_output:
            self.layers_list.append(Flatten())

        # Build all layers
        for layer in self.layers_list:
            layer.build(input_shape)
            input_shape = layer.compute_output_shape(input_shape)

        super().build(input_shape)

    def call(self, inputs):
        x = inputs
        for layer in self.layers_list:
            x = layer(x)
        return x

    def compute_linear_equivalent_weights(self):
        equivalent_weights = keras.ops.zeros((self.input_seq_len, self.input_features, self.output_len, self.output_features))
        equivalent_bias = self.call(keras.ops.zeros((1, self.input_seq_len, self.input_features)))[0]
    
        for i in range(self.input_seq_len):
            for j in range(self.input_features):
                input_tensor = keras.ops.zeros((1, self.input_seq_len, self.input_features))
                input_tensor = input_tensor.at[0, i, j].set(1.0)
                output = self.call(input_tensor)
                equivalent_weights = equivalent_weights.at[i, j].set(output[0] - equivalent_bias)
    
        return equivalent_weights, equivalent_bias

    def get_linear_equivalent_model(self):
        equivalent_weights, equivalent_bias = self.compute_linear_equivalent_weights()
        
        input_layer = Input(shape=(self.input_seq_len, self.input_features))
        linear_layer = LinearLayer(equivalent_weights, equivalent_bias)
        output = linear_layer(input_layer)
        
        linear_model = keras.Model(inputs=input_layer, outputs=output)
        
        # Freeze the model
        linear_model.trainable = False
        
        return linear_model

In [33]:
compare_models(
    generate = lambda sequence_length, n_ahead: get_hourly_dataset(input_steps = sequence_length, output_steps = n_ahead, mode = "S", add_time_information = False),
    models=['LinearNet'],
    exp_name="etth1_linearnet_results/etth1_univariate_without_time_temporary",
    n_run=1
)
exp_name_tmp = "etth1_linearnet_results/etth1_univariate_without_time_temporary_"
for file_end in ['r2_avg.parquet', 'r2_std.parquet', 'rmse_avg.parquet', 'rmse_std.parquet', 'time_avg.parquet', 'time_std.parquet', 'num_params.parquet']:
    tmp_df = pd.read_parquet(exp_name_tmp + file_end)
    result_df = pd.read_parquet(exp_name_tmp.replace('temporary_','') + file_end)
    result_df.loc[tmp_df.index,tmp_df.columns] = tmp_df
    result_df.to_parquet(exp_name_tmp.replace('temporary_','') + file_end)
    del tmp_df
    del result_df

compare_models(
    generate = lambda sequence_length, n_ahead: get_hourly_dataset(input_steps = sequence_length, output_steps = n_ahead, mode = "S", add_time_information = True),
    models=['LinearNet'],
    exp_name="etth1_linearnet_results/etth1_univariate_with_time_temporary",
    n_run=1
)
exp_name_tmp = "etth1_linearnet_results/etth1_univariate_with_time_temporary_"
for file_end in ['r2_avg.parquet', 'r2_std.parquet', 'rmse_avg.parquet', 'rmse_std.parquet', 'time_avg.parquet', 'time_std.parquet', 'num_params.parquet']:
    tmp_df = pd.read_parquet(exp_name_tmp + file_end)
    result_df = pd.read_parquet(exp_name_tmp.replace('temporary_','') + file_end)
    result_df.loc[tmp_df.index,tmp_df.columns] = tmp_df
    result_df.to_parquet(exp_name_tmp.replace('temporary_','') + file_end)
    del tmp_df
    del result_df

compare_models(
    generate = lambda sequence_length, n_ahead: get_hourly_dataset(input_steps = sequence_length, output_steps = n_ahead, mode = "MS", add_time_information = False),
    models=['LinearNet'],
    exp_name="etth1_linearnet_results/etth1_multivariate_without_time_temporary",
    n_run=1
)
exp_name_tmp = "etth1_linearnet_results/etth1_multivariate_without_time_temporary_"
for file_end in ['r2_avg.parquet', 'r2_std.parquet', 'rmse_avg.parquet', 'rmse_std.parquet', 'time_avg.parquet', 'time_std.parquet', 'num_params.parquet']:
    tmp_df = pd.read_parquet(exp_name_tmp + file_end)
    result_df = pd.read_parquet(exp_name_tmp.replace('temporary_','') + file_end)
    result_df.loc[tmp_df.index,tmp_df.columns] = tmp_df
    result_df.to_parquet(exp_name_tmp.replace('temporary_','') + file_end)
    del tmp_df
    del result_df

compare_models(
    generate = lambda sequence_length, n_ahead: get_hourly_dataset(input_steps = sequence_length, output_steps = n_ahead, mode = "MS", add_time_information = True),
    models=['LinearNet'],
    exp_name="etth1_linearnet_results/etth1_multivariate_with_time_temporary",
    n_run=1
)
exp_name_tmp = "etth1_linearnet_results/etth1_multivariate_with_time_temporary_"
for file_end in ['r2_avg.parquet', 'r2_std.parquet', 'rmse_avg.parquet', 'rmse_std.parquet', 'time_avg.parquet', 'time_std.parquet', 'num_params.parquet']:
    tmp_df = pd.read_parquet(exp_name_tmp + file_end)
    result_df = pd.read_parquet(exp_name_tmp.replace('temporary_','') + file_end)
    result_df.loc[tmp_df.index,tmp_df.columns] = tmp_df
    result_df.to_parquet(exp_name_tmp.replace('temporary_','') + file_end)
    del tmp_df
    del result_df

Sequence Length: 3, Model: LinearNet, N_ahead: 1, Run: 1, Time: 9.31s, RMSE: 0.0941
Sequence Length: 3, Model: LinearNet, N_ahead: 6, Run: 1, Time: 7.48s, RMSE: 0.1655
Sequence Length: 3, Model: LinearNet, N_ahead: 15, Run: 1, Time: 7.75s, RMSE: 0.2248
Sequence Length: 3, Model: LinearNet, N_ahead: 30, Run: 1, Time: 6.94s, RMSE: 0.2603
Sequence Length: 3, Model: LinearNet, N_ahead: 90, Run: 1, Time: 5.85s, RMSE: 0.3465
Sequence Length: 3, Model: LinearNet, N_ahead: 180, Run: 1, Time: 5.22s, RMSE: 0.3901
Sequence Length: 3, Model: LinearNet, N_ahead: 360, Run: 1, Time: 4.86s, RMSE: 0.4471
Sequence Length: 10, Model: LinearNet, N_ahead: 1, Run: 1, Time: 10.49s, RMSE: 0.0935
Sequence Length: 10, Model: LinearNet, N_ahead: 6, Run: 1, Time: 10.67s, RMSE: 0.1608
Sequence Length: 10, Model: LinearNet, N_ahead: 15, Run: 1, Time: 7.05s, RMSE: 0.2105
Sequence Length: 10, Model: LinearNet, N_ahead: 30, Run: 1, Time: 8.00s, RMSE: 0.2527
Sequence Length: 10, Model: LinearNet, N_ahead: 90, Run: 1, T

model                   LinearNet
n_ahead sequence_length          
1       3                0.986606
        10               0.986761
        20               0.987061
        50               0.987246
        100               0.98768
        200              0.987869
        400              0.987724
6       3                0.955988
        10               0.958606
        20               0.962532
        50               0.964872
        100              0.966548
        200              0.967693
        400              0.967828
15      3                0.918921
        10               0.929491
        20               0.934273
        50               0.939783
        100              0.942676
        200              0.943939
        400              0.943994
30      3                0.892337
        10               0.898562
        20                0.90561
        50               0.908977
        100               0.91661
        200              0.918795
        400              0.915187
90      3                 0.80813
        10               0.819436
        20               0.831859
        50               0.834637
        100              0.859084
        200              0.861492
        400              0.865399
180     3                0.757232
        10               0.775521
        20               0.776468
        50               0.808272
        100              0.822209
        200              0.834191
        400              0.828131
360     3                 0.67746
        10               0.713018
        20                0.72416
        50               0.756863
        100              0.771418
        200              0.781033
        400              0.785466

R2 Scores Std:


model                   LinearNet
n_ahead sequence_length          
1       3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0
6       3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0
15      3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0
30      3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0
90      3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0
180     3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0
360     3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0


RMSE Scores Average:


...

model                    LinearNet
n_ahead sequence_length           
1       3                 8.388933
        10               11.265287
        20               10.167243
        50               10.782688
        100               8.249568
        200              13.559207
        400              13.638251
6       3                 7.270499
        10               10.181846
        20                9.661096
        50               11.146904
        100                10.0431
        200                11.0434
        400              11.787323
15      3                 8.320535
        10                9.206914
        20                8.187497
        50                7.796754
        100               8.933979
        200               10.81566
        400              10.360705
30      3                 8.149175
        10                8.809142
        20                7.845387
        50                8.747061
        100               8.988961
        200               9.871216
        400               8.270468
90      3                 6.691637
        10                6.852556
        20                6.953032
        50                7.471233
        100               7.689288
        200               9.272154
        400               8.996646
180     3                  7.24491
        10                6.872154
        20                6.740479
        50                6.956288
        100               7.522039
        200               7.435975
        400               7.425296
360     3                 6.390133
        10                6.717214
        20                 6.60487
        50                7.038222
        100               7.260517
        200               6.884879
        400               6.550785


Training Times Std:


model                   LinearNet
n_ahead sequence_length          
1       3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0
6       3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0
15      3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0
30      3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0
90      3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0
180     3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0
360     3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0


Number of Parameters:


model                   LinearNet
n_ahead sequence_length          
1       3                  1066.0
        10                 1108.0
        20                 1168.0
        50                 1348.0
        100                1648.0
        200                2248.0
        400                3448.0
6       3                  1161.0
        10                 1238.0
        20                 1348.0
        50                 1678.0
        100                2228.0
        200                3328.0
        400                5528.0
15      3                  1458.0
        10                 1598.0
        20                 1798.0
        50                 2398.0
        100                3398.0
        200                5398.0
        400                9398.0
30      3                  2313.0
        10                 2558.0
        20                 2908.0
        50                 3958.0
        100                5708.0
        200                9208.0
        400               16208.0
90      3                 10233.0
        10                10898.0
        20                11848.0
        50                14698.0
        100               19448.0
        200               28948.0
        400               47948.0
180     3                 35613.0
        10                36908.0
        20                38758.0
        50                44308.0
        100               53558.0
        200               72058.0
        400              109058.0
360     3                134973.0
        10               137528.0
        20               141178.0
        50               152128.0
        100              170378.0
        200              206878.0
        400              279878.0

In [35]:
df = pd.read_parquet('/workspace/data.parquet')
df = df[(df.index >= pd.Timestamp('2020-01-01')) & (df.index < pd.Timestamp('2023-01-01'))]
assets = ['BTC']
df = df[[c for c in df.columns if 'quote asset volume' in c and any(asset in c for asset in assets)]]
df.columns = [c.replace(' quote asset volume', '') for c in df.columns]
compare_models(
    generate = lambda sequence_length, n_ahead: generate_data(df = df, sequence_length = sequence_length, n_ahead = n_ahead),
    models=['LinearNet'],
    exp_name="btc_linearnet_results/btc_univariate_without_time_temporary",
    n_run=1
)
exp_name_tmp = "btc_linearnet_results/btc_univariate_without_time_temporary_"
for file_end in ['r2_avg.parquet', 'r2_std.parquet', 'rmse_avg.parquet', 'rmse_std.parquet', 'time_avg.parquet', 'time_std.parquet', 'num_params.parquet']:
    tmp_df = pd.read_parquet(exp_name_tmp + file_end)
    result_df = pd.read_parquet(exp_name_tmp.replace('temporary_','') + file_end)
    result_df.loc[tmp_df.index,tmp_df.columns] = tmp_df
    result_df.to_parquet(exp_name_tmp.replace('temporary_','') + file_end)
    del tmp_df
    del result_df


df = pd.read_parquet('/workspace/data.parquet')
df = df[(df.index >= pd.Timestamp('2020-01-01')) & (df.index < pd.Timestamp('2023-01-01'))]
assets = ['BTC']
df = df[[c for c in df.columns if 'quote asset volume' in c and any(asset in c for asset in assets)]]
df['hour'] = df.reset_index()['group'].apply(lambda x: x.hour).values
df['dayofweek'] = df.reset_index()['group'].apply(lambda x: x.dayofweek).values
df.columns = [c.replace(' quote asset volume', '') for c in df.columns]
compare_models(
    generate = lambda sequence_length, n_ahead: generate_data(df = df, sequence_length = sequence_length, n_ahead = n_ahead),
    models=['LinearNet'],
    exp_name="btc_linearnet_results/btc_univariate_with_time_temporary",
    n_run=1
)
exp_name_tmp = "btc_linearnet_results/btc_univariate_with_time_temporary_"
for file_end in ['r2_avg.parquet', 'r2_std.parquet', 'rmse_avg.parquet', 'rmse_std.parquet', 'time_avg.parquet', 'time_std.parquet', 'num_params.parquet']:
    tmp_df = pd.read_parquet(exp_name_tmp + file_end)
    result_df = pd.read_parquet(exp_name_tmp.replace('temporary_','') + file_end)
    result_df.loc[tmp_df.index,tmp_df.columns] = tmp_df
    result_df.to_parquet(exp_name_tmp.replace('temporary_','') + file_end)
    del tmp_df
    del result_df

df = pd.read_parquet('/workspace/data.parquet')
df = df[(df.index >= pd.Timestamp('2020-01-01')) & (df.index < pd.Timestamp('2023-01-01'))]
assets = ['BTC', 'ETH', 'ADA', 'XMR', 'EOS', 'MATIC', 'TRX', 'FTM', 'BNB', 'XLM', 'ENJ', 'CHZ', 'BUSD', 'ATOM', 'LINK', 'ETC', 'XRP', 'BCH', 'LTC']
df = df[[c for c in df.columns if 'quote asset volume' in c and any(asset in c for asset in assets)]]
df.columns = [c.replace(' quote asset volume', '') for c in df.columns]
compare_models(
    generate = lambda sequence_length, n_ahead: generate_data(df = df, sequence_length = sequence_length, n_ahead = n_ahead),
    models=['LinearNet'],
    exp_name="btc_linearnet_results/btc_multivariate_without_time_temporary",
    n_run=1
)
exp_name_tmp = "btc_linearnet_results/btc_multivariate_without_time_temporary_"
for file_end in ['r2_avg.parquet', 'r2_std.parquet', 'rmse_avg.parquet', 'rmse_std.parquet', 'time_avg.parquet', 'time_std.parquet', 'num_params.parquet']:
    tmp_df = pd.read_parquet(exp_name_tmp + file_end)
    result_df = pd.read_parquet(exp_name_tmp.replace('temporary_','') + file_end)
    result_df.loc[tmp_df.index,tmp_df.columns] = tmp_df
    result_df.to_parquet(exp_name_tmp.replace('temporary_','') + file_end)
    del tmp_df
    del result_df

df = pd.read_parquet('/workspace/data.parquet')
df = df[(df.index >= pd.Timestamp('2020-01-01')) & (df.index < pd.Timestamp('2023-01-01'))]
assets = ['BTC', 'ETH', 'ADA', 'XMR', 'EOS', 'MATIC', 'TRX', 'FTM', 'BNB', 'XLM', 'ENJ', 'CHZ', 'BUSD', 'ATOM', 'LINK', 'ETC', 'XRP', 'BCH', 'LTC']
df = df[[c for c in df.columns if 'quote asset volume' in c and any(asset in c for asset in assets)]]
df.columns = [c.replace(' quote asset volume', '') for c in df.columns]
df['hour'] = df.reset_index()['group'].apply(lambda x: x.hour).values
df['dayofweek'] = df.reset_index()['group'].apply(lambda x: x.dayofweek).values
compare_models(
    generate = lambda sequence_length, n_ahead: generate_data(df = df, sequence_length = sequence_length, n_ahead = n_ahead),
    models=['LinearNet'],
    exp_name="btc_linearnet_results/btc_multivariate_with_time_temporary",
    n_run=1
)
exp_name_tmp = "btc_linearnet_results/btc_multivariate_with_time_temporary_"
for file_end in ['r2_avg.parquet', 'r2_std.parquet', 'rmse_avg.parquet', 'rmse_std.parquet', 'time_avg.parquet', 'time_std.parquet', 'num_params.parquet']:
    tmp_df = pd.read_parquet(exp_name_tmp + file_end)
    result_df = pd.read_parquet(exp_name_tmp.replace('temporary_','') + file_end)
    result_df.loc[tmp_df.index,tmp_df.columns] = tmp_df
    result_df.to_parquet(exp_name_tmp.replace('temporary_','') + file_end)
    del tmp_df
    del result_df


Sequence Length: 3, Model: LinearNet, N_ahead: 1, Run: 1, Time: 7.24s, RMSE: 0.0544
Sequence Length: 3, Model: LinearNet, N_ahead: 6, Run: 1, Time: 7.28s, RMSE: 0.0659
Sequence Length: 3, Model: LinearNet, N_ahead: 15, Run: 1, Time: 7.22s, RMSE: 0.0684
Sequence Length: 3, Model: LinearNet, N_ahead: 30, Run: 1, Time: 6.50s, RMSE: 0.0696
Sequence Length: 3, Model: LinearNet, N_ahead: 90, Run: 1, Time: 6.33s, RMSE: 0.0654
Sequence Length: 3, Model: LinearNet, N_ahead: 180, Run: 1, Time: 6.36s, RMSE: 0.0531
Sequence Length: 3, Model: LinearNet, N_ahead: 360, Run: 1, Time: 6.62s, RMSE: 0.0449
Sequence Length: 10, Model: LinearNet, N_ahead: 1, Run: 1, Time: 7.62s, RMSE: 0.0547
Sequence Length: 10, Model: LinearNet, N_ahead: 6, Run: 1, Time: 7.03s, RMSE: 0.0657
Sequence Length: 10, Model: LinearNet, N_ahead: 15, Run: 1, Time: 7.25s, RMSE: 0.0676
Sequence Length: 10, Model: LinearNet, N_ahead: 30, Run: 1, Time: 6.74s, RMSE: 0.0689
Sequence Length: 10, Model: LinearNet, N_ahead: 90, Run: 1, Tim

model                   LinearNet
n_ahead sequence_length          
1       3                0.409234
        10               0.403156
        20               0.411653
        50               0.415184
        100              0.413607
        200              0.412898
        400              0.403918
6       3                0.133661
        10               0.139498
        20               0.166782
        50                0.17229
        100              0.169032
        200              0.181879
        400              0.173903
15      3                0.070154
        10               0.092582
        20               0.115326
        50               0.111654
        100              0.113108
        200              0.128415
        400              0.126757
30      3                0.052746
        10               0.073709
        20               0.086351
        50               0.087686
        100              0.089005
        200              0.102587
        400              0.105037
90      3                0.030173
        10               0.044328
        20                0.05412
        50               0.058034
        100              0.066104
        200              0.079849
        400              0.090696
180     3                 0.03026
        10               0.047918
        20               0.060373
        50               0.069685
        100              0.081221
        200              0.105156
        400              0.113369
360     3                0.023661
        10               0.034671
        20               0.044305
        50               0.053941
        100               0.06552
        200              0.082953
        400               0.08793

R2 Scores Std:


model                   LinearNet
n_ahead sequence_length          
1       3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0
6       3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0
15      3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0
30      3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0
90      3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0
180     3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0
360     3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0


RMSE Scores Average:


...

model                    LinearNet
n_ahead sequence_length           
1       3                  7.75355
        10                7.801464
        20                8.187626
        50               11.269605
        100               9.991112
        200              12.487424
        400              15.378929
6       3                 7.813691
        10                9.380783
        20                8.688362
        50               12.068322
        100              12.035253
        200              11.758544
        400              17.497478
15      3                 9.390032
        10                8.999938
        20                9.266819
        50               10.913952
        100               12.58603
        200              14.046673
        400              13.609134
30      3                 9.440223
        10                9.577143
        20               11.129122
        50               10.594795
        100              11.394423
        200              11.168608
        400              14.740262
90      3                 7.818063
        10                7.965226
        20                8.348605
        50                9.220402
        100              10.182802
        200              10.983263
        400               11.59905
180     3                 8.546959
        10                7.671487
        20                8.433186
        50                9.001698
        100               9.765564
        200               9.803268
        400              11.853604
360     3                 8.852021
        10                 8.65169
        20                8.726762
        50                9.709296
        100                10.3528
        200              11.767786
        400               9.801882


Training Times Std:


model                   LinearNet
n_ahead sequence_length          
1       3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0
6       3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0
15      3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0
30      3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0
90      3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0
180     3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0
360     3                     0.0
        10                    0.0
        20                    0.0
        50                    0.0
        100                   0.0
        200                   0.0
        400                   0.0


Number of Parameters:


model                   LinearNet
n_ahead sequence_length          
1       3                  5632.0
        10                 5674.0
        20                 5734.0
        50                 5914.0
        100                6214.0
        200                6814.0
        400                8014.0
6       3                  5727.0
        10                 5804.0
        20                 5914.0
        50                 6244.0
        100                6794.0
        200                7894.0
        400               10094.0
15      3                  6024.0
        10                 6164.0
        20                 6364.0
        50                 6964.0
        100                7964.0
        200                9964.0
        400               13964.0
30      3                  6879.0
        10                 7124.0
        20                 7474.0
        50                 8524.0
        100               10274.0
        200               13774.0
        400               20774.0
90      3                 14799.0
        10                15464.0
        20                16414.0
        50                19264.0
        100               24014.0
        200               33514.0
        400               52514.0
180     3                 40179.0
        10                41474.0
        20                43324.0
        50                48874.0
        100               58124.0
        200               76624.0
        400              113624.0
360     3                139539.0
        10               142094.0
        20               145744.0
        50               156694.0
        100              174944.0
        200              211444.0
        400              284444.0